In [ ]:
import os, re
import numpy as np
import pandas as pd

import sklearn
from sklearn.linear_model import LinearRegression # for solving for scaling /centering values
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error # if squared=False; RMSE

import os
import optuna
import pickle as pkl

import tqdm

from joblib import Parallel, delayed # Oputna has parallelism built in but for training replicates of the selected model
# I'll run them through Parallel

import plotly.express as px
import plotly.graph_objects as go

In [ ]:
cache_path = './notebook_artifacts/5_ensembling/'

shared_out_path = './data/Shared_Model_Output'

# Level 1 Modeling: ID prediction files

## Blup Predictions

In [ ]:
blup_yhats = [e for e in os.listdir(shared_out_path) if re.findall('.+BlupYHats.csv', e)]
blup_yhats = [e for e in blup_yhats if re.findall('\d+', e)]

In [ ]:
# task 1. For each BlupYHat file, get the corresponding phno_ref 

file_name = 'Ws20163BlupYHats.csv'

def load_blup_yhats(file_name):
    df = pd.read_csv(shared_out_path + '/'+ file_name
                    ).rename(columns = {'Unnamed: 0': 'Ind',
                                       'Yield_Mg_ha': 'Yield_Mg_ha_Scaled',
                                       'YHat': 'YHat_Scaled'})
    blup_yhats_dig = re.findall('\d+', file_name)[0]    
    df['Class'] = re.findall('\D+', file_name)[0]   
    df['CV'] = blup_yhats_dig[0:4]
    df['Rep'] = blup_yhats_dig[-1]
    ref = pd.read_csv('./data/Processed/phno_ref_'+str(blup_yhats_dig[0:4])+'_small.csv'
               ).rename(columns = {'Unnamed: 0': 'Ind'})

    df = ref.merge(df, how = 'outer')
    
    # solve for the scaling /centering values
    vals = df.loc[:, ['Yield_Mg_ha', 'Yield_Mg_ha_Scaled']].dropna()
    val_x = vals[['Yield_Mg_ha_Scaled']]
    val_y = vals[['Yield_Mg_ha']]

    reg = LinearRegression().fit(val_x, val_y)
    center_val = reg.intercept_[0]
    scale_val = reg.coef_[0][0]
    
    df['Center'] = center_val
    df['Scale'] = scale_val
    
    df['YHat'] = (df['YHat_Scaled']*scale_val) + center_val

    return(df)

df = load_blup_yhats(file_name = 'Ws20163BlupYHats.csv')
df

In [ ]:
def calc_blup_rmses(df):
    """
    This code assumes columns 'Year', 'Yield_Mg_ha', 'YHat'
    """
    def blup_groupby_rmse(df):
        #https://stackoverflow.com/questions/47914428/python-dataframe-calculating-r2-and-rmse-using-groupby-on-one-column
        return(sklearn.metrics.mean_squared_error(df['Yield_Mg_ha'], df['YHat'], squared = False))

    df_rmses = df.loc[:, ['Year', 'Yield_Mg_ha', 'YHat']].dropna().groupby('Year'
                ).apply(blup_groupby_rmse).reset_index().rename(columns = {0:'RMSE'})
    df_rmses = df_rmses.merge(df.loc[:, ['Class', 'CV', 'Rep']], right_index=True, left_index = True)
    return(df_rmses)

In [ ]:
calc_blup_rmses(df)

Year      RMSE Class    CV Rep
0  2014  2.070225    Ws  2016   3
1  2015  1.926574    Ws  2016   3
2  2016  3.875080    Ws  2016   3
3  2017  2.000900    Ws  2016   3
4  2018  2.841473    Ws  2016   3
5  2019  2.513721    Ws  2016   3
6  2020  2.464064    Ws  2016   3
7  2021  2.932006    Ws  2016   3

In [ ]:
blup_rmse_overview = pd.concat([calc_blup_rmses(df) for df in [load_blup_yhats(e) for e in blup_yhats]])
blup_rmse_overview

Year      RMSE Class    CV Rep
0   2014  3.265076    As  2021   1
1   2015  2.684606    As  2021   1
2   2016  2.678364    As  2021   1
3   2017  3.012884    As  2021   1
4   2018  3.206836    As  2021   1
..   ...       ...   ...   ...  ..
3   2017  3.013192    As  2021   2
4   2018  3.207226    As  2021   2
5   2019  3.588968    As  2021   2
6   2020  2.838363    As  2021   2
7   2021  3.406370    As  2021   2

[384 rows x 5 columns]

## Random Forests

In [ ]:
rf_yhats = [e for e in os.listdir(shared_out_path) if re.findall('rf\d\d\d\d_\drfYHats.csv', e)]

## XGBoost

In [ ]:
xgb_yhats = [e for e in os.listdir(shared_out_path) if re.findall('xgb\d\d\d\d_\dxgbYHats.csv', e)]

## DNNs

In [ ]:
# Placeholder

## Historical

In [ ]:
hist_yhats = [e for e in os.listdir(shared_out_path) if re.findall('hist\d\d\d\d_\dYHats.csv', e)]

# Level 2 Modeling: Collect Predictions

## No BLUP version 

In [ ]:
# data for merging predictions into
phno = pd.read_csv('./data/Processed/phno3.csv')
phno.head()

Env  Year       Hybrid  Yield_Mg_ha
0  DEH1_2014  2014  M0088/LH185     5.721725
1  DEH1_2014  2014  M0143/LH185    11.338246
2  DEH1_2014  2014  M0003/LH185     6.540810
3  DEH1_2014  2014  M0035/LH185    10.366857
4  DEH1_2014  2014  M0052/LH185    10.908814

### Identify Files

In [ ]:
# from a list get model 
def parse_yhat_filename(in_str = 'rf2017_5rfYHats.csv'):
    in_str = re.findall('^\D+\d+_\d', in_str)[0]
    mod = re.findall('^\D+', in_str)[0]
    cv, rep = in_str.replace(mod, '').split('_')
    return([mod, cv, rep])

In [ ]:
rf_yhats_groups = pd.concat([
    # get mod, cv, rep for all rf_yhats, set col to be the ith file processed
    pd.DataFrame([parse_yhat_filename(e) for e in rf_yhats][i]).rename(columns = {0:i}) 
    # merge dfs
    for i in range(len(rf_yhats))], axis = 1)

rf_yhats_groups = rf_yhats_groups.T.rename(columns = {0:'Mod', 1:'CV', 2:'Rep'})
rf_yhats_groups['File'] = rf_yhats

rf_yhats_groups.head()

Mod    CV Rep                 File
0  rf  2017   5  rf2017_5rfYHats.csv
1  rf  2016   8  rf2016_8rfYHats.csv
2  rf  2015   4  rf2015_4rfYHats.csv
3  rf  2019   3  rf2019_3rfYHats.csv
4  rf  2020   8  rf2020_8rfYHats.csv

In [ ]:
xgb_yhats_groups = pd.concat([
    # get mod, cv, rep for all xgb_yhats, set col to be the ith file processed
    pd.DataFrame([parse_yhat_filename(e) for e in xgb_yhats][i]).rename(columns = {0:i}) 
    # merge dfs
    for i in range(len(xgb_yhats))], axis = 1)

xgb_yhats_groups = xgb_yhats_groups.T.rename(columns = {0:'Mod', 1:'CV', 2:'Rep'})
xgb_yhats_groups['File'] = xgb_yhats

xgb_yhats_groups.head()

Mod    CV Rep                   File
0  xgb  2015   1  xgb2015_1xgbYHats.csv
1  xgb  2021   4  xgb2021_4xgbYHats.csv
2  xgb  2021   7  xgb2021_7xgbYHats.csv
3  xgb  2015   5  xgb2015_5xgbYHats.csv
4  xgb  2016   9  xgb2016_9xgbYHats.csv

In [ ]:
hist_yhats_groups = pd.concat([
    # get mod, cv, rep for all hist_yhats, set col to be the ith file processed
    pd.DataFrame([parse_yhat_filename(e) for e in hist_yhats][i]).rename(columns = {0:i}) 
    # merge dfs
    for i in range(len(hist_yhats))], axis = 1)

hist_yhats_groups = hist_yhats_groups.T.rename(columns = {0:'Mod', 1:'CV', 2:'Rep'})
hist_yhats_groups['File'] = hist_yhats

hist_yhats_groups.head()

Mod    CV Rep                 File
0  hist  2019   6  hist2019_6YHats.csv
1  hist  2015   6  hist2015_6YHats.csv
2  hist  2020   1  hist2020_1YHats.csv
3  hist  2021   9  hist2021_9YHats.csv
4  hist  2021   5  hist2021_5YHats.csv

### Parse files

In [ ]:
# Parse the prediction file, reverse scaling and optionally rename (e.g. with the model/cv/rep)

def get_ml_yhats(file_name = 'rf2017_5rfYHats.csv',
                 rename_Yhat = None,
                file_path = shared_out_path):
    df = pd.read_csv(file_path+'/'+file_name)

    # solve for the scaling /centering values
    vals = df.loc[:, ['Yield_Mg_ha', 'YMat']].dropna()
    val_x = vals[['YMat']]
    val_y = vals[['Yield_Mg_ha']]

    reg = LinearRegression().fit(val_x, val_y)
    center_val = reg.intercept_[0]
    scale_val = reg.coef_[0][0]

    df['Center'] = center_val
    df['Scale'] = scale_val

    df['YHat_Mg_ha'] = (df['YHat']*scale_val) + center_val
    df = df.loc[:, ['Env', 'Year', 'Hybrid', 'Yield_Mg_ha', 'YHat_Mg_ha']]

    if rename_Yhat == None:
        return(df)
    else:
        return(df.rename(columns = {'YHat_Mg_ha': rename_Yhat}))



In [ ]:
# aggregate all rf predictions
# pull select cols from each file then merge
rf_yhats_df = [get_ml_yhats(file_name = rf_yhat,
                                      rename_Yhat = rf_yhat.replace('rfYHats.csv', '')
                ) for rf_yhat in tqdm.tqdm(rf_yhats)]

# This is messy but the alternative is to repeatedly merge
# drop select cols from all but 0th data frame so they are not duplicated in 
# in the yhat df
rf_yhats_df = pd.concat([rf_yhats_df[e] if e == 0 else 
                         rf_yhats_df[e].drop(columns = [
                             'Env', 'Year', 'Hybrid', 'Yield_Mg_ha']) 
                         for e in range(0, len(rf_yhats_df))], axis = 1)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 80/80 [00:10<00:00,  7.73it/s]


In [ ]:
# Repeat for xgb
xgb_yhats_df = [get_ml_yhats(file_name = xgb_yhat,
                                      rename_Yhat = xgb_yhat.replace('xgbYHats.csv', '')
                ) for xgb_yhat in tqdm.tqdm(xgb_yhats)]

xgb_yhats_df = pd.concat([xgb_yhats_df[e] if e == 0 else 
                         xgb_yhats_df[e].drop(columns = [
                             'Env', 'Year', 'Hybrid', 'Yield_Mg_ha']) 
                         for e in range(0, len(xgb_yhats_df))], axis = 1)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 80/80 [00:08<00:00,  8.98it/s]


In [ ]:
xgb_yhats_df

Env  Year             Hybrid  Yield_Mg_ha  xgb2015_1  xgb2021_4  \
0       DEH1_2014  2014        M0088/LH185     5.721725   9.174236   9.218873   
1       DEH1_2014  2014        M0143/LH185    11.338246  12.836893  12.605838   
2       DEH1_2014  2014        M0003/LH185     6.540810   9.769042   9.690945   
3       DEH1_2014  2014        M0035/LH185    10.366857   9.685836   9.806112   
4       DEH1_2014  2014        M0052/LH185    10.908814  11.040541  10.872248   
...           ...   ...                ...          ...        ...        ...   
138258  WIH3_2022  2022  W10010_0337/LH244          NaN   9.735470   9.532347   
138259  WIH3_2022  2022  W10010_0346/LH244          NaN   9.735470   9.532347   
138260  WIH3_2022  2022  W10010_0358/LH244          NaN   9.735470   9.532347   
138261  WIH3_2022  2022  W10010_0381/LH244          NaN   9.735470   9.532347   
138262  WIH3_2022  2022  W10010_0452/LH244          NaN   9.735470   9.532347   

        xgb2021_7  xgb2015_5  xgb2016_9  xgb2020_4  ...  xgb2015_9  xgb2018_2  \
0        9.218873   9.174236   9.273191   9.170669  ...   9.174236   9.369481   
1       12.605838  12.836893  12.501812  12.711792  ...  12.836893  12.494710   
2        9.690945   9.769042   9.804429   9.763325  ...   9.769042   9.686178   
3        9.806112   9.685836   9.748226   9.693987  ...   9.685836   9.697983   
4       10.872248  11.040541  10.982620  10.860308  ...  11.040541  11.078245   
...           ...        ...        ...        ...  ...        ...        ...   
138258   9.532347   9.735470   4.288635   9.940990  ...   9.735470  11.734806   
138259   9.532347   9.735470   4.288635   9.940990  ...   9.735470  11.734806   
138260   9.532347   9.735470   4.288635   9.940990  ...   9.735470  11.734806   
138261   9.532347   9.735470   4.288635   9.940990  ...   9.735470  11.734806   
138262   9.532347   9.735470   4.288635   9.940990  ...   9.735470  11.734806   

        xgb2020_5  xgb2014_7  xgb2017_0  xgb2015_8  xgb2021_3  xgb2014_9  \
0        9.170669   7.866826   9.137220   9.174236   9.218873   7.866826   
1       12.711792   7.858380  12.485730  12.836893  12.605838   7.858380   
2        9.763325   7.927887   9.670136   9.769042   9.690945   7.927887   
3        9.693987   7.972298   9.712099   9.685836   9.806112   7.972298   
4       10.860308   8.022842  10.893131  11.040541  10.872248   8.022842   
...           ...        ...        ...        ...        ...        ...   
138258   9.940990  13.290309   8.498224   9.735470   9.532347  13.290309   
138259   9.940990  13.290309   8.498224   9.735470   9.532347  13.290309   
138260   9.940990  13.290309   8.498224   9.735470   9.532347  13.290309   
138261   9.940990  13.290309   8.498224   9.735470   9.532347  13.290309   
138262   9.940990  13.290309   8.498224   9.735470   9.532347  13.290309   

        xgb2015_6  xgb2015_2  
0        9.174236   9.174236  
1       12.836893  12.836893  
2        9.769042   9.769042  
3        9.685836   9.685836  
4       11.040541  11.040541  
...           ...        ...  
138258   9.735470   9.735470  
138259   9.735470   9.735470  
138260   9.735470   9.735470  
138261   9.735470   9.735470  
138262   9.735470   9.735470  

[138263 rows x 84 columns]

In [ ]:
# Repeat for hist
hist_yhats_df = [get_ml_yhats(file_name = hist_yhat,
                                      rename_Yhat = hist_yhat.replace('histYHats.csv', '')
                ) for hist_yhat in tqdm.tqdm(hist_yhats)]

hist_yhats_df = pd.concat([hist_yhats_df[e] if e == 0 else 
                         hist_yhats_df[e].drop(columns = [
                             'Env', 'Year', 'Hybrid', 'Yield_Mg_ha']) 
                         for e in range(0, len(hist_yhats_df))], axis = 1)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 80/80 [00:09<00:00,  8.44it/s]


In [ ]:
hist_yhats_df = hist_yhats_df.drop_duplicates()

### Agg extracted predictions

In [ ]:
yHats_df = pd.concat([
    phno, 
    rf_yhats_df.drop(columns =  ['Env', 'Year', 'Hybrid', 'Yield_Mg_ha']),
    xgb_yhats_df.drop(columns = ['Env', 'Year', 'Hybrid', 'Yield_Mg_ha'])
], axis = 1)

yHats_df.head()

Env  Year       Hybrid  Yield_Mg_ha   rf2017_5   rf2016_8   rf2015_4  \
0  DEH1_2014  2014  M0088/LH185     5.721725  10.591565  11.412896  11.685779   
1  DEH1_2014  2014  M0143/LH185    11.338246  11.995944  11.639840  11.685779   
2  DEH1_2014  2014  M0003/LH185     6.540810  10.605881  11.549416  11.685779   
3  DEH1_2014  2014  M0035/LH185    10.366857  11.623779  11.524263  11.685779   
4  DEH1_2014  2014  M0052/LH185    10.908814  12.024014  11.639840  11.685779   

    rf2019_3   rf2020_8   rf2016_1  ...  xgb2015_9  xgb2018_2  xgb2020_5  \
0  11.641665  12.045789  11.209850  ...   9.174236   9.369481   9.170669   
1  11.922401  12.045789  11.623760  ...  12.836893  12.494710  12.711792   
2  11.887824  12.045789  11.398859  ...   9.769042   9.686178   9.763325   
3  11.901552  12.045789  11.539536  ...   9.685836   9.697983   9.693987   
4  11.922401  12.045789  11.621606  ...  11.040541  11.078245  10.860308   

   xgb2014_7  xgb2017_0  xgb2015_8  xgb2021_3  xgb2014_9  xgb2015_6  xgb2015_2  
0   7.866826   9.137220   9.174236   9.218873   7.866826   9.174236   9.174236  
1   7.858380  12.485730  12.836893  12.605838   7.858380  12.836893  12.836893  
2   7.927887   9.670136   9.769042   9.690945   7.927887   9.769042   9.769042  
3   7.972298   9.712099   9.685836   9.806112   7.972298   9.685836   9.685836  
4   8.022842  10.893131  11.040541  10.872248   8.022842  11.040541  11.040541  

[5 rows x 164 columns]

In [ ]:
# note constraining to entries with historical data reduces the number of obs #--NOTE--
# not done for submisson 1
yHats_df = yHats_df.merge(hist_yhats_df)

In [ ]:
yHats_notBlup = yHats_df

## Blup Version

In [ ]:
def reformat_blup_filename(file_name = 'Ws20141BlupYHats.csv'):
    file_name = file_name.replace('BlupYHats.csv', '')
    file_digits = re.findall('\d+', file_name)[0]  
    file_class  = re.findall('\D+', file_name)[0]   
    file_year = file_digits[0:4]
    file_rep = file_digits[-1]
    return(file_class+file_year+'_'+file_rep)
        
# reformat_blup_filename(file_name = 'Ws20141BlupYHats.csv')

In [ ]:
# get predictions in the same format as for the ml models. 
# Note that it contains the functionality to return or not return the index in
# phno for confirming data is appropriately matched.
def get_blup_yhats(file_name = 'Ws20141BlupYHats.csv',
                   rename_Yhat = None, #'Ws2014_1'
                   return_Ind = True
                  ):
    df = pd.read_csv(shared_out_path + '/'+ file_name
                    ).rename(columns = {'Unnamed: 0': 'Ind',
                                       'Yield_Mg_ha': 'Yield_Mg_ha_Scaled',
                                       'YHat': 'YHat_Scaled'})
    blup_yhats_dig = re.findall('\d+', file_name)[0]    
    df['Class'] = re.findall('\D+', file_name)[0]   
    df['CV'] = blup_yhats_dig[0:4]
    df['Rep'] = blup_yhats_dig[-1]
    ref = pd.read_csv('./data/Processed/phno_ref_'+str(blup_yhats_dig[0:4])+'_small.csv'
               ).rename(columns = {'Unnamed: 0': 'Ind'})

    df = ref.merge(df, how = 'outer')

    # solve for the scaling /centering values
    vals = df.loc[:, ['Yield_Mg_ha', 'Yield_Mg_ha_Scaled']].dropna()
    val_x = vals[['Yield_Mg_ha_Scaled']]
    val_y = vals[['Yield_Mg_ha']]

    reg = LinearRegression().fit(val_x, val_y)
    center_val = reg.intercept_[0]
    scale_val = reg.coef_[0][0]

    df['Center'] = center_val
    df['Scale'] = scale_val

    df['YHat_Mg_ha'] = (df['YHat_Scaled']*scale_val) + center_val
    
    if return_Ind:
        df = df.loc[:, ['Ind', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha', 'YHat_Mg_ha']]
    else:
        df = df.loc[:, [       'Env', 'Hybrid', 'Year', 'Yield_Mg_ha', 'YHat_Mg_ha']]

    if rename_Yhat == None:
        return(df)
    else:
        return(df.rename(columns = {'YHat_Mg_ha': rename_Yhat}))

# get_blup_yhats(file_name = 'Ws20141BlupYHats.csv',
#                rename_Yhat = 'Ws2014_1')

In [ ]:
# Repeat pattern for differently formatted data
blup_yhats_df = [get_blup_yhats(
    file_name = e,
    rename_Yhat = reformat_blup_filename(file_name = e),
#     return_Ind = False
    return_Ind = True
) for e in blup_yhats]

blup_yhats_df = pd.concat([blup_yhats_df[e] if e == 0 else 
                         blup_yhats_df[e].drop(columns = [
                             e for e in list(blup_yhats_df[e]) if e in [
                                 'Ind', 'Env', 'Year', 'Hybrid', 'Yield_Mg_ha'
                             ]]) 
                         for e in range(0, len(blup_yhats_df))], axis = 1)

In [ ]:
# Make sure there's at most one prediction for each set of identifiers
# replace with a filler number so that when it I group on yield these rows aren't dropped
mask = (blup_yhats_df.Year == 2022)
blup_yhats_df.loc[mask, 'Yield_Mg_ha'] = -9999

blup_yhats_df = blup_yhats_df.drop(columns = ['Ind']
                            ).groupby(['Env', 'Hybrid', 'Year', 'Yield_Mg_ha']
                            ).agg(np.mean).reset_index()

# undo
mask = (blup_yhats_df.Year == 2022)
blup_yhats_df.loc[mask, 'Yield_Mg_ha'] = np.nan
# confirm there are no negative yield values before proceeding
assert np.nanmin(blup_yhats_df.Yield_Mg_ha) > 0 

### Agg extracted predictions

In [ ]:
# note there are more entries per keys in phno than in blup_yhats_df. That's okay.
tmp = blup_yhats_df.merge(phno.reset_index()).rename(columns = {'index':'phno_Idx'})
tmp = tmp.merge(rf_yhats_df, how = 'left').drop_duplicates()
tmp = tmp.merge(xgb_yhats_df, how = 'left').drop_duplicates()

tmp = tmp.merge(hist_yhats_df, how = 'left').drop_duplicates()
# TODO add more -- 

# reorder cols
first_cols = ['phno_Idx', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']
tmp = tmp.loc[:, first_cols+[e for e in list(tmp) if e not in first_cols]]
tmp.head()
# 22791  

phno_Idx        Env    Hybrid  Year  Yield_Mg_ha   As2021_1  Ws2014_1  \
0       442  DEH1_2014  B37/MO17  2014    13.074965   9.121875  9.344017   
1       170  DEH1_2014  B37/MO17  2014    14.269989   9.121875  9.344016   
2       443  DEH1_2014  B37/OH43  2014    12.733455   8.888700  9.344017   
3       159  DEH1_2014  B37/OH43  2014    12.888180   8.888700  9.344017   
4       154  DEH1_2014  B73/MO17  2014    11.916843  10.059382  9.344019   

    As2018_3   As2019_2   Ws2021_1  ...  hist2020_5YHats.csv  \
0   9.358152   9.010285  12.512784  ...            11.565516   
1   9.358152   9.010285  12.512782  ...            11.565516   
2   8.923334   8.740011  12.512784  ...            12.256507   
3   8.923334   8.740011  12.512784  ...            12.256507   
4  10.327831  10.276469  12.512784  ...            13.403211   

   hist2016_7YHats.csv  hist2017_2YHats.csv  hist2018_4YHats.csv  \
0            11.754089            12.019373            12.081095   
1            11.754089            12.019373            12.081095   
2            11.836908            12.023243            12.189115   
3            11.836908            12.023243            12.189115   
4            13.128523            12.398731            12.510930   

   hist2016_2YHats.csv  hist2015_7YHats.csv  hist2017_1YHats.csv  \
0            11.792728            12.127767            12.069353   
1            11.792728            12.127767            12.069353   
2            11.693192            12.057645            12.036624   
3            11.693192            12.057645            12.036624   
4            13.274353            12.323332            12.437433   

   hist2015_5YHats.csv  hist2016_8YHats.csv  hist2018_2YHats.csv  
0            12.037796            11.787248            12.080966  
1            12.037796            11.787248            12.080966  
2            12.098830            11.739069            12.133405  
3            12.098830            11.739069            12.133405  
4            12.342596            13.152802            12.435341  

[5 rows x 293 columns]

In [ ]:
yHats_yesBlup = tmp

# Prepare covariates

In [ ]:
save_path = './data/Processed/'

# phno = pd.read_csv(save_path+"phno3.csv")

YMat = np.load(save_path+'YMat3.npy')
GMat = np.load(save_path+'GMat3.npy')
SMat = np.load(save_path+'SMat3.npy')
WMat = np.load(save_path+'WMat3.npy')
MMat = np.load(save_path+'MMat3.npy')

GMatNames = np.load(save_path+'GMatNames.npy')
SMatNames = np.load(save_path+'SMatNames.npy')
WMatNames = np.load(save_path+'WMatNames.npy')
MMatNames = np.load(save_path+'MMatNames.npy')

In [ ]:
# create backups in case I overwrite the covariate matrices
phno_backup = phno

YMat_backup = YMat
GMat_backup = GMat
SMat_backup = SMat
WMat_backup = WMat
MMat_backup = MMat

GMatNames_backup = GMatNames
SMatNames_backup = SMatNames
WMatNames_backup = WMatNames
MMatNames_backup = MMatNames

In [ ]:
def restrict_mats(phno_idxs = [], # list of indices to be used. If [] passed make no change
                  phno = phno_backup,
                  YMat = YMat_backup,
                  GMat = GMat_backup,
                  SMat = SMat_backup,
                  WMat = WMat_backup,
                  MMat = MMat_backup):
    # reduce and reset indices
    if phno_idxs == []:
        pass
    else:
        phno = phno.loc[phno_idxs, ].reset_index().rename(columns = {'index': 'phno_idxs'})
        YMat = YMat[phno_idxs]
        GMat = GMat[phno_idxs]
        SMat = SMat[phno_idxs]
        WMat = WMat[phno_idxs]
        MMat = MMat[phno_idxs]
    return(phno, YMat, GMat, SMat, WMat, MMat)

# Restrict to obs used for BLUPs
# phno, YMat, GMat, SMat, WMat, MMat = restrict_mats(
#     phno_idxs = list(tmp.phno_Idx), # list of indices to be used. If [] passed make no change
#     phno = phno_backup,
#     YMat = YMat_backup,
#     GMat = GMat_backup,
#     SMat = SMat_backup,
#     WMat = WMat_backup,
#     MMat = MMat_backup)

# Ensembling Models

## yHats_yesBlup

In [ ]:
yHats_yesBlup

phno_Idx        Env             Hybrid  Year  Yield_Mg_ha   As2021_1  \
0           442  DEH1_2014           B37/MO17  2014    13.074965   9.121875   
1           170  DEH1_2014           B37/MO17  2014    14.269989   9.121875   
2           443  DEH1_2014           B37/OH43  2014    12.733455   8.888700   
3           159  DEH1_2014           B37/OH43  2014    12.888180   8.888700   
4           154  DEH1_2014           B73/MO17  2014    11.916843  10.059382   
...         ...        ...                ...   ...          ...        ...   
22786    138258  WIH3_2022  W10010_0337/LH244  2022          NaN   9.789351   
22787    138259  WIH3_2022  W10010_0346/LH244  2022          NaN   9.816483   
22788    138260  WIH3_2022  W10010_0358/LH244  2022          NaN   9.825012   
22789    138261  WIH3_2022  W10010_0381/LH244  2022          NaN   9.877398   
22790    138262  WIH3_2022  W10010_0452/LH244  2022          NaN   9.811505   

        Ws2014_1   As2018_3   As2019_2   Ws2021_1  ...  hist2020_5YHats.csv  \
0       9.344017   9.358152   9.010285  12.512784  ...            11.565516   
1       9.344016   9.358152   9.010285  12.512782  ...            11.565516   
2       9.344017   8.923334   8.740011  12.512784  ...            12.256507   
3       9.344017   8.923334   8.740011  12.512784  ...            12.256507   
4       9.344019  10.327831  10.276469  12.512784  ...            13.403211   
...          ...        ...        ...        ...  ...                  ...   
22786  10.098443  10.157472  10.262061  11.738350  ...             9.365567   
22787  10.098443  10.208021  10.294339  11.738350  ...             9.365567   
22788  10.098443  10.316085  10.434624  11.738350  ...             9.365567   
22789  10.098443  10.342616  10.462092  11.738350  ...             9.365567   
22790  10.098443  10.264919  10.361201  11.738350  ...             9.365567   

       hist2016_7YHats.csv  hist2017_2YHats.csv  hist2018_4YHats.csv  \
0                11.754089            12.019373            12.081095   
1                11.754089            12.019373            12.081095   
2                11.836908            12.023243            12.189115   
3                11.836908            12.023243            12.189115   
4                13.128523            12.398731            12.510930   
...                    ...                  ...                  ...   
22786             7.675474            10.163933            10.004684   
22787             7.675474            10.163933            10.004684   
22788             7.675474            10.163933            10.004684   
22789             7.675474            10.163933            10.004684   
22790             7.675474            10.163933            10.004684   

       hist2016_2YHats.csv  hist2015_7YHats.csv  hist2017_1YHats.csv  \
0                11.792728            12.127767            12.069353   
1                11.792728            12.127767            12.069353   
2                11.693192            12.057645            12.036624   
3                11.693192            12.057645            12.036624   
4                13.274353            12.323332            12.437433   
...                    ...                  ...                  ...   
22786             6.896305            10.585495            10.264088   
22787             6.896305            10.585495            10.264088   
22788             6.896305            10.585495            10.264088   
22789             6.896305            10.585495            10.264088   
22790             6.896305            10.585495            10.264088   

       hist2015_5YHats.csv  hist2016_8YHats.csv  hist2018_2YHats.csv  
0                12.037796            11.787248            12.080966  
1                12.037796            11.787248            12.080966  
2                12.098830            11.739069            12.133405  
3                12.098830            11.739069            12.133405  
4                12.3425

In [ ]:
phno, YMat, GMat, SMat, WMat, MMat = restrict_mats(
    phno_idxs = list(yHats_yesBlup.phno_Idx), # list of indices to be used. If [] passed make no change
    phno = phno_backup,
    YMat = YMat_backup,
    GMat = GMat_backup,
    SMat = SMat_backup,
    WMat = WMat_backup,
    MMat = MMat_backup)

### Simplest thing that might work

Average with respect to 
Within model type
within hold out year
across hold out years

In [ ]:
# ens_cols = [e for e in list(yHats_yesBlup) if e not in ['phno_Idx', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']]
# This is hardcoded to ensure the results are reproducible
ens_cols = ['As2021_1', 'Ws2014_1', 'As2018_3', 'As2019_2', 'Ws2021_1', 'As2017_2', 
            'Ws2017_1', 'Ws2020_1', 'As2014_1', 'Ws2018_1', 'As2016_3', 'Ws2017_3', 
            'As2018_1', 'Ws2019_3', 'As2018_2', 'Ws2021_3', 'Ws2014_3', 'Ws2019_1', 
            'Ws2015_3', 'As2014_2', 'Ws2021_2', 'Ws2018_2', 'As2015_3', 'As2020_1', 
            'As2019_1', 'Ws2016_1', 'As2020_3', 'Ws2018_3', 'Ws2014_2', 'As2016_1', 
            'Ws2015_2', 'As2021_3', 'Ws2015_1', 'Ws2017_2', 'As2019_3', 'As2016_2', 
            'As2014_3', 'Ws2020_3', 'As2015_1', 'Ws2016_3', 'As2017_3', 'As2017_1', 
            'Ws2019_2', 'As2020_2', 'Ws2020_2', 'Ws2016_2', 'As2015_2', 'As2021_2', 
            'rf2017_5', 'rf2016_8', 'rf2015_4', 'rf2019_3', 'rf2020_8', 'rf2016_1', 
            'rf2019_9', 'rf2015_1', 'rf2020_3', 'rf2015_7', 'rf2021_6', 'rf2018_8', 
            'rf2017_7', 'rf2021_9', 'rf2015_5', 'rf2020_1', 'rf2017_8', 'rf2015_2', 
            'rf2015_0', 'rf2014_8', 'rf2020_5', 'rf2019_1', 'rf2020_4', 'rf2016_0', 
            'rf2014_9', 'rf2021_4', 'rf2014_4', 'rf2021_2', 'rf2016_3', 'rf2014_5', 
            'rf2019_4', 'rf2020_6', 'rf2019_2', 'rf2017_4', 'rf2016_6', 'rf2018_0', 
            'rf2020_0', 'rf2015_3', 'rf2021_0', 'rf2019_7', 'rf2018_1', 'rf2016_7', 
            'rf2021_5', 'rf2019_6', 'rf2014_3', 'rf2017_2', 'rf2018_4', 'rf2018_7', 
            'rf2017_9', 'rf2015_8', 'rf2018_6', 'rf2017_0', 'rf2021_1', 'rf2014_6', 
            'rf2020_7', 'rf2016_9', 'rf2018_3', 'rf2016_5', 'rf2017_1', 'rf2017_6', 
            'rf2021_7', 'rf2018_9', 'rf2014_7', 'rf2015_6', 'rf2019_8', 'rf2014_0', 
            'rf2016_2', 'rf2021_8', 'rf2020_9', 'rf2018_5', 'rf2015_9', 'rf2018_2', 
            'rf2014_2', 'rf2021_3', 'rf2016_4', 'rf2020_2', 'rf2014_1', 'rf2017_3', 
            'rf2019_5', 'rf2019_0', 'xgb2015_1', 'xgb2021_4', 'xgb2021_7', 'xgb2015_5', 
            'xgb2016_9', 'xgb2020_4', 'xgb2017_3', 'xgb2018_1', 'xgb2017_5', 'xgb2019_3', 
            'xgb2018_0', 'xgb2021_9', 'xgb2014_1', 'xgb2020_0', 'xgb2020_9', 'xgb2018_7', 
            'xgb2018_8', 'xgb2015_4', 'xgb2016_0', 'xgb2021_1', 'xgb2018_4', 'xgb2019_8', 
            'xgb2015_7', 'xgb2020_2', 'xgb2017_1', 'xgb2016_8', 'xgb2014_3', 'xgb2021_2', 
            'xgb2016_1', 'xgb2019_5', 'xgb2017_8', 'xgb2018_3', 'xgb2021_6', 'xgb2015_0', 
            'xgb2019_1', 'xgb2018_5', 'xgb2014_5', 'xgb2019_9', 'xgb2020_6', 'xgb2020_8', 
            'xgb2015_3', 'xgb2019_2', 'xgb2014_6', 'xgb2016_2', 'xgb2017_7', 'xgb2016_4', 
            'xgb2021_0', 'xgb2014_2', 'xgb2014_4', 'xgb2016_3', 'xgb2020_1', 'xgb2019_0', 
            'xgb2021_8', 'xgb2017_2', 'xgb2014_0', 'xgb2019_7', 'xgb2019_4', 'xgb2018_6', 
            'xgb2018_9', 'xgb2014_8', 'xgb2020_3', 'xgb2016_6', 'xgb2017_6', 'xgb2016_7', 
            'xgb2021_5', 'xgb2017_9', 'xgb2019_6', 'xgb2017_4', 'xgb2016_5', 'xgb2020_7', 
            'xgb2015_9', 'xgb2018_2', 'xgb2020_5', 'xgb2014_7', 'xgb2017_0', 'xgb2015_8', 
            'xgb2021_3', 'xgb2014_9', 'xgb2015_6', 'xgb2015_2']


ens_cols_info = pd.DataFrame(zip(
    ens_cols,
    [re.findall('\d\d\d\d', e)[0] for e in list(ens_cols)],
    [re.findall('^\D+', e)[0] for e in list(ens_cols)],
    [re.findall('\d+$', e)[0] for e in list(ens_cols)]
)).rename(columns = {0:'Model_Name', 1:'Holdout_Year', 2:'Model', 3:'Rep',})

ens_cols_info

tmp = yHats_yesBlup

id_vars = ['phno_Idx', 'Env', 'Hybrid', 'Year']

tmp = tmp.melt(id_vars=id_vars, 
               value_vars=[e for e in list(tmp) if e not in id_vars],
               var_name='Model_Name', value_name='yHat')

tmp = tmp.merge(ens_cols_info, how = 'left')

tmp.head(5)

phno_Idx        Env    Hybrid  Year   Model_Name       yHat Holdout_Year  \
0       442  DEH1_2014  B37/MO17  2014  Yield_Mg_ha  13.074965          NaN   
1       170  DEH1_2014  B37/MO17  2014  Yield_Mg_ha  14.269989          NaN   
2       443  DEH1_2014  B37/OH43  2014  Yield_Mg_ha  12.733455          NaN   
3       159  DEH1_2014  B37/OH43  2014  Yield_Mg_ha  12.888180          NaN   
4       154  DEH1_2014  B73/MO17  2014  Yield_Mg_ha  11.916843          NaN   

  Model  Rep  
0   NaN  NaN  
1   NaN  NaN  
2   NaN  NaN  
3   NaN  NaN  
4   NaN  NaN

In [ ]:
# average replicates
tmp = tmp.groupby(id_vars+['Holdout_Year', 'Model']).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year Holdout_Year Model       yHat
0       153  DEH1_2014  PHG39/PHN82  2014         2014    As  10.288905
1       153  DEH1_2014  PHG39/PHN82  2014         2014    Ws   9.515110
2       153  DEH1_2014  PHG39/PHN82  2014         2014    rf   8.443935
3       153  DEH1_2014  PHG39/PHN82  2014         2014   xgb   9.375648
4       153  DEH1_2014  PHG39/PHN82  2014         2015    As  10.335568

In [ ]:
# average over model types
tmp = tmp.groupby(id_vars+['Holdout_Year']).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year Holdout_Year       yHat
0       153  DEH1_2014  PHG39/PHN82  2014         2014   9.405900
1       153  DEH1_2014  PHG39/PHN82  2014         2015  11.081915
2       153  DEH1_2014  PHG39/PHN82  2014         2016  11.098123
3       153  DEH1_2014  PHG39/PHN82  2014         2017  11.274013
4       153  DEH1_2014  PHG39/PHN82  2014         2018  11.129524

In [ ]:
# average over holdout years
tmp = tmp.groupby(id_vars).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year       yHat
0       153  DEH1_2014  PHG39/PHN82  2014  10.935842
1       154  DEH1_2014     B73/MO17  2014  12.083079
2       156  DEH1_2014  PHW52/PHM49  2014  11.422641
3       157  DEH1_2014    B73/PHN82  2014  11.844031
4       158  DEH1_2014   LH74/PHN82  2014  11.251343

In [ ]:
tmp

phno_Idx        Env             Hybrid  Year       yHat
0           153  DEH1_2014        PHG39/PHN82  2014  10.935842
1           154  DEH1_2014           B73/MO17  2014  12.083079
2           156  DEH1_2014        PHW52/PHM49  2014  11.422641
3           157  DEH1_2014          B73/PHN82  2014  11.844031
4           158  DEH1_2014         LH74/PHN82  2014  11.251343
...         ...        ...                ...   ...        ...
22786    138258  WIH3_2022  W10010_0337/LH244  2022  10.133647
22787    138259  WIH3_2022  W10010_0346/LH244  2022  10.161746
22788    138260  WIH3_2022  W10010_0358/LH244  2022  10.177265
22789    138261  WIH3_2022  W10010_0381/LH244  2022  10.186711
22790    138262  WIH3_2022  W10010_0452/LH244  2022  10.156792

[22791 rows x 5 columns]

In [ ]:
def format_submission(df = tmp,
                      yhat_col = 'yHat'
):
    sub_template = pd.read_csv('./data/Maize_GxE_Competition_Data/Testing_Data/1_Submission_Template_2022.csv')
    tmp = sub_template.drop(columns = ['Yield_Mg_ha']).merge(df, how = 'left')
    tmp['Yield_Mg_ha'] = tmp[yhat_col]
    tmp = tmp.loc[:, ['Env', 'Hybrid', 'Yield_Mg_ha']]
    return(tmp)

In [ ]:
first_submission = format_submission(
    df = tmp,
    yhat_col = 'yHat')

In [ ]:
if False:
    first_submission.to_csv('./notebook_artifacts/99_submissions/Submission_1.csv', index = 'False')

### Test with RF (unoptimized)

In [ ]:
yHats_yesBlup

phno_Idx        Env             Hybrid  Year  Yield_Mg_ha   As2021_1  \
0           442  DEH1_2014           B37/MO17  2014    13.074965   9.121875   
1           170  DEH1_2014           B37/MO17  2014    14.269989   9.121875   
2           443  DEH1_2014           B37/OH43  2014    12.733455   8.888700   
3           159  DEH1_2014           B37/OH43  2014    12.888180   8.888700   
4           154  DEH1_2014           B73/MO17  2014    11.916843  10.059382   
...         ...        ...                ...   ...          ...        ...   
22786    138258  WIH3_2022  W10010_0337/LH244  2022          NaN   9.789351   
22787    138259  WIH3_2022  W10010_0346/LH244  2022          NaN   9.816483   
22788    138260  WIH3_2022  W10010_0358/LH244  2022          NaN   9.825012   
22789    138261  WIH3_2022  W10010_0381/LH244  2022          NaN   9.877398   
22790    138262  WIH3_2022  W10010_0452/LH244  2022          NaN   9.811505   

        Ws2014_1   As2018_3   As2019_2   Ws2021_1  ...  hist2020_5YHats.csv  \
0       9.344017   9.358152   9.010285  12.512784  ...            11.565516   
1       9.344016   9.358152   9.010285  12.512782  ...            11.565516   
2       9.344017   8.923334   8.740011  12.512784  ...            12.256507   
3       9.344017   8.923334   8.740011  12.512784  ...            12.256507   
4       9.344019  10.327831  10.276469  12.512784  ...            13.403211   
...          ...        ...        ...        ...  ...                  ...   
22786  10.098443  10.157472  10.262061  11.738350  ...             9.365567   
22787  10.098443  10.208021  10.294339  11.738350  ...             9.365567   
22788  10.098443  10.316085  10.434624  11.738350  ...             9.365567   
22789  10.098443  10.342616  10.462092  11.738350  ...             9.365567   
22790  10.098443  10.264919  10.361201  11.738350  ...             9.365567   

       hist2016_7YHats.csv  hist2017_2YHats.csv  hist2018_4YHats.csv  \
0                11.754089            12.019373            12.081095   
1                11.754089            12.019373            12.081095   
2                11.836908            12.023243            12.189115   
3                11.836908            12.023243            12.189115   
4                13.128523            12.398731            12.510930   
...                    ...                  ...                  ...   
22786             7.675474            10.163933            10.004684   
22787             7.675474            10.163933            10.004684   
22788             7.675474            10.163933            10.004684   
22789             7.675474            10.163933            10.004684   
22790             7.675474            10.163933            10.004684   

       hist2016_2YHats.csv  hist2015_7YHats.csv  hist2017_1YHats.csv  \
0                11.792728            12.127767            12.069353   
1                11.792728            12.127767            12.069353   
2                11.693192            12.057645            12.036624   
3                11.693192            12.057645            12.036624   
4                13.274353            12.323332            12.437433   
...                    ...                  ...                  ...   
22786             6.896305            10.585495            10.264088   
22787             6.896305            10.585495            10.264088   
22788             6.896305            10.585495            10.264088   
22789             6.896305            10.585495            10.264088   
22790             6.896305            10.585495            10.264088   

       hist2015_5YHats.csv  hist2016_8YHats.csv  hist2018_2YHats.csv  
0                12.037796            11.787248            12.080966  
1                12.037796            11.787248            12.080966  
2                12.098830            11.739069            12.133405  
3                12.098830            11.739069            12.133405  
4                12.3425

In [ ]:
EMat = np.array(yHats_yesBlup.drop(columns = ['phno_Idx', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']))
EMatNames =list(yHats_yesBlup.drop(columns = ['phno_Idx', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']))

In [ ]:
# transform to panel data
def wthr_rank_3to2(x_3d):
    n_obs, n_days, n_metrics = x_3d.shape
    return(x_3d.reshape(n_obs, (n_days*n_metrics)))

def wthr_features_rank_2to3(x_3d, feature_import):
    n_obs, n_days, n_metrics = x_3d.shape
    return(feature_import.reshape(n_days, n_metrics))

def y_rank_2to1(y_2d):
    n_obs = y_2d.shape[0]
    return(y_2d.reshape(n_obs, ))

In [ ]:
def prep_ensemble_train_test(
    test_this_year = '2014',
    downsample = False, 
    downsample_train = 1000,
    downsample_test  =  100,
    phno = phno,
    GMat = GMat,
    SMat = SMat,
    WMat = WMat,
    MMat = MMat,
    EMat = EMat, # <----------------------- Add ensemble matrix
    YMat = YMat
):

    mask_undefined = (phno.Yield_Mg_ha.isna()) # these can be imputed but not evaluated
    mask_test = ((phno.Year == int(test_this_year)) & (~mask_undefined))
    mask_train = ((phno.Year != int(test_this_year)) & (~mask_undefined))
    test_idx = phno.loc[mask_test, ].index
    train_idx = phno.loc[mask_train, ].index

    if downsample:
        train_idx = np.random.choice(train_idx, downsample_train)
        test_idx = np.random.choice(test_idx, downsample_test)


    # Get Scalings ---------------------------------------------------------------
    YMat_center = np.mean(YMat[train_idx], axis = 0)
    YMat_scale = np.std(YMat[train_idx], axis = 0)

    SMat_center = np.mean(SMat[train_idx, :], axis = 0)
    SMat_scale = np.std(SMat[train_idx, :], axis = 0)

    WMat_center = np.mean(WMat[train_idx, :, :], axis = 0)
    WMat_scale = np.std(WMat[train_idx, :, :], axis = 0)

    MMat_center = np.nanmean(MMat[train_idx, :], axis = 0)
    MMat_scale = np.nanstd(MMat[train_idx, :], axis = 0)
    # if std is 0, set to 1
    MMat_scale[MMat_scale == 0] = 1

    EMat_center = np.mean(EMat[train_idx, :], axis = 0)
    EMat_scale = np.std(EMat[train_idx, :], axis = 0)
    
    # Center and Scale -----------------------------------------------------------
    YMat = (YMat - YMat_center)/YMat_scale
    SMat = (SMat - SMat_center)/SMat_scale
    MMat = (MMat - MMat_center)/MMat_scale
    EMat = (EMat - EMat_center)/EMat_scale

    # Split ------------------------------------------------------------------
    train_g = GMat[train_idx, :]
    test_g  = GMat[test_idx, :]

    train_s = SMat[train_idx, :]
    test_s  = SMat[test_idx, :]

    train_w = WMat[train_idx, :, :]
    test_w  = WMat[test_idx, :, :]

    train_m = MMat[train_idx, :]
    test_m  = MMat[test_idx, :]

    train_y = YMat[train_idx]
    test_y  = YMat[test_idx]

    train_e = EMat[train_idx, :]
    test_e  = EMat[test_idx, :]
    
    # Reshape to rank 1
    train_y = train_y.reshape([train_y.shape[0], 1])
    test_y = test_y.reshape([test_y.shape[0], 1])

    # GSWM
    train_x_2d = np.concatenate([train_g, train_s, wthr_rank_3to2(x_3d = train_w), train_m, train_e], axis = 1)
    train_y_1d = y_rank_2to1(y_2d = train_y)
    test_x_2d = np.concatenate([test_g, test_s, wthr_rank_3to2(x_3d = test_w), test_m, test_e], axis = 1)
    test_y_1d = y_rank_2to1(y_2d = test_y)
    
    full_x_2d = np.concatenate([GMat, SMat, wthr_rank_3to2(x_3d = WMat), MMat, EMat], axis = 1)
    return(train_x_2d, train_y_1d, test_x_2d, test_y_1d, full_x_2d, YMat_center, YMat_scale, YMat)


In [ ]:
test_x_2d_names = list(GMatNames)+list(SMatNames)+list(WMatNames)+list(MMatNames)+list(EMatNames)

In [ ]:
# find name in EMatNames that have the test year, all others should be removed
# e.g. if cv == 2021, then the model should only have yhats that were produced
#      with a test year of 2021
def get_non_cv_cols(test_this_year = 2022,
                    EMatNames = EMatNames,
                    test_x_2d_names = test_x_2d_names):
    rm_cols = [e for e in EMatNames if not re.match('\D+'+str(test_this_year)+'_\d', e)]
    select_col_idxs = [i for i in range(len(test_x_2d_names)) if test_x_2d_names[i] not in rm_cols]
    return(select_col_idxs)

In [ ]:
# Setup ----------------------------------------------------------------------
trial_name = 'enybr' # ensemble, yes blup, random forest
n_trials= 120 #FIXME
n_jobs = 30  #FIXME

downsample = False
downsample_train = 1000
downsample_test  =  100

def objective(trial): 
    rf_max_depth = trial.suggest_int('rf_max_depth', 2, 100, log=True)
    rf_n_estimators = trial.suggest_int('rf_n_estimators', 20, 100, log=True)
    rf_min_samples_split = trial.suggest_float('rf_min_samples_split', 0.005, 0.5, log=True)
    
    regr = RandomForestRegressor(
        max_depth = rf_max_depth, 
        n_estimators = rf_n_estimators,
        min_samples_split = rf_min_samples_split
        )
    
#     rf = regr.fit(train_x_2d, train_y_1d)
#     return (mean_squared_error(train_y_1d, rf.predict(train_x_2d), squared=False))
    rf = regr.fit(test_x_2d, test_y_1d)
    return (mean_squared_error(test_y_1d, rf.predict(test_x_2d), squared=False))


if False:
    reset_trial_name = trial_name
    print("""
    ------------------------------------------------------------------------------
               Note: Ensemble fit using previous test fold.
    ------------------------------------------------------------------------------
    """)
    for test_this_year in ['2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021']:
        print("""
    ------------------------------------------
    ------------------"""+test_this_year+"""------------------
        """)    

        trial_name = reset_trial_name
        trial_name = trial_name+test_this_year
        print(test_this_year)
        # Data Prep. -----------------------------------------------------------------
        # Set up train/test indices --------------------------------------------------
        train_x_2d, train_y_1d, test_x_2d, test_y_1d, full_x_2d, YMat_center, YMat_scale, YMat = prep_ensemble_train_test(
                test_this_year = test_this_year,
                downsample = downsample, 
                downsample_train = downsample_train,
                downsample_test  =  downsample_test,
                phno = phno,
                GMat = GMat,
                SMat = SMat,
                WMat = WMat,
                MMat = MMat,
                EMat = EMat,
                YMat = YMat)

        test_year_cols = get_non_cv_cols(
            test_this_year = test_this_year,
            EMatNames = EMatNames,
            test_x_2d_names = test_x_2d_names)

        # excise columns that would allow for information leakage into the 
        train_x_2d = train_x_2d[:, np.array(test_year_cols)]
        test_x_2d  =  test_x_2d[:, np.array(test_year_cols)]
        full_x_2d  =  full_x_2d[:, np.array(test_year_cols)]


        # HPS Study ------------------------------------------------------------------
        cache_save_name = cache_path+trial_name+'_hps.pkl'
        if os.path.exists(cache_save_name):
            study = pkl.load(open(cache_save_name, 'rb'))  
        else:
            study = optuna.create_study(direction="minimize")
            study.optimize(objective, n_trials= n_trials, n_jobs = n_jobs)
            # save    
            pkl.dump(study, open(cache_save_name, 'wb'))    

        print("""
    --------------Study Complete--------------
    ------------------------------------------
        """)
        def fit_single_rep(Rep = 1):
            # Fit Best HPS --------------------------------------------------------------- 
            cache_save_name = cache_path+trial_name+'_'+str(Rep)+'_mod.pkl'

            # Load cached model if it exists
            if os.path.exists(cache_save_name):
                rf = pkl.load(open(cache_save_name, 'rb'))  
            else:
                regr = RandomForestRegressor(
                        max_depth = study.best_trial.params['rf_max_depth'], 
                        n_estimators = study.best_trial.params['rf_n_estimators'],
                        min_samples_split = study.best_trial.params['rf_min_samples_split']
                        )
    #             rf = regr.fit(train_x_2d, train_y_1d)
                rf = regr.fit(test_x_2d, test_y_1d)
                # save    
                pkl.dump(rf, open(cache_save_name, 'wb'))   

            # Record Predictions -----------------------------------------------------
            out = phno.copy()
            out['YHat'] = rf.predict(full_x_2d)
            out['YMat'] = YMat
            out['Y_center'] = YMat_center
            out['Y_scale'] = YMat_scale
            out['Class'] = trial_name
            out['CV'] = test_this_year
            out['Rep'] = Rep
            out.to_csv('./notebook_artifacts/5_ensembling/'+trial_name+'_'+str(Rep)+'YHats.csv')
    #         out.to_csv('./data/Shared_Model_Output/'+trial_name+'_'+str(Rep)+'rfYHats.csv')

        # use joblib to get replicate models all at once
        Parallel(n_jobs=10)(delayed(fit_single_rep)(Rep = i) for i in range(10))

In [ ]:
enybr_yhats = [e for e in os.listdir(cache_path) if re.match('enybr\d\d\d\d_\dYHats.csv', e)] 

In [ ]:
# aggregate all enybr predictions
# pull select cols from each file then merge
enybr_yhats_df = [get_ml_yhats(file_name = enybr_yhat,
                               rename_Yhat = enybr_yhat.replace('YHats.csv', ''),
                               file_path = cache_path
                ) for enybr_yhat in tqdm.tqdm(enybr_yhats)]

# This is messy but the alternative is to repeatedly merge
# drop select cols from all but 0th data frame so they are not duplicated in 
# in the yhat df
enybr_yhats_df = pd.concat([enybr_yhats_df[e] if e == 0 else 
                         enybr_yhats_df[e].drop(columns = [
                             'Env', 'Year', 'Hybrid', 'Yield_Mg_ha']) 
                         for e in range(0, len(enybr_yhats_df))], axis = 1)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 80/80 [00:01<00:00, 48.11it/s]


In [ ]:
enybr_yhats_df_backup = enybr_yhats_df.copy()
enybr_yhats_df_backup

Env  Year             Hybrid  Yield_Mg_ha  enybr2016_6  \
0      DEH1_2014  2014           B37/MO17    13.074965     5.531932   
1      DEH1_2014  2014           B37/MO17    14.269989     5.531932   
2      DEH1_2014  2014           B37/OH43    12.733455     5.177942   
3      DEH1_2014  2014           B37/OH43    12.888180     5.177942   
4      DEH1_2014  2014           B73/MO17    11.916843     6.977406   
...          ...   ...                ...          ...          ...   
22786  WIH3_2022  2022  W10010_0337/LH244          NaN     8.466721   
22787  WIH3_2022  2022  W10010_0346/LH244          NaN     8.466721   
22788  WIH3_2022  2022  W10010_0358/LH244          NaN     8.466721   
22789  WIH3_2022  2022  W10010_0381/LH244          NaN     8.466721   
22790  WIH3_2022  2022  W10010_0452/LH244          NaN     8.466721   

       enybr2020_9  enybr2015_4  enybr2018_1  enybr2016_5  enybr2018_0  ...  \
0         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
1         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
2         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
3         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
4        10.242690     8.729195    10.017510     7.130188    10.296167  ...   
...            ...          ...          ...          ...          ...  ...   
22786     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22787     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22788     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22789     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22790     9.065231     8.584796     8.757695     8.612560     8.327171  ...   

       enybr2018_7  enybr2018_8  enybr2016_4  enybr2019_8  enybr2015_1  \
0         8.818321     8.744628     5.420871    12.111806     8.031712   
1         8.818321     8.744628     5.420871    12.111806     8.031712   
2         7.945677     7.859318     4.824092    11.049220     7.907455   
3         7.945677     7.859318     4.824092    11.049220     7.907455   
4         9.823241     9.661137     6.576953    12.570122     8.631707   
...            ...          ...          ...          ...          ...   
22786     8.935659     8.222512     8.786011     9.137428     8.964489   
22787     8.935659     8.222512     8.786011     9.137428     8.964489   
22788     8.935659     8.222512     8.786011     9.137428     8.964489   
22789     8.935659     8.222512     8.786011     9.137428     8.964489   
22790     8.935659     8.222512     8.786011     9.137428     8.964489   

       enybr2020_6  enybr2017_3  enybr2014_6  enybr2017_2  enybr2016_8  
0         8.645928     8.236111    13.707251     8.432482     5.097374  
1         8.645928     8.236111    13.707251     8.432482     5.097374  
2         8.866839     7.920904    12.711938     7.810802     5.050909  
3         8.866839     7.920904    12.711938     7.810802     5.050909  
4        10.393625     8.635470    14.786144     8.663692     6.833022  
...            ...          ...          ...          ...          ...  
22786     9.688920     8.459518    11.311052     8.739894     8.355336  
22787     9.688920     8.459518    11.311052     8.739894     8.355336  
22788     9.688920     8.459518    11.311052     8.739894     8.355336  
22789     9.688920     8.459518    11.311052     8.739894     8.355336  
22790     9.688920     8.459518    11.311052     8.739894     8.355336  

[22791 rows x 84 columns]

In [ ]:
# returns uniform weights across years and replicates within years

def ens_unif_yearwise_weight(current_year, 
                            df):
    mask = (df.Year == current_year)
#     y_true = df.loc[mask, 'Yield_Mg_ha']
    current_cols = [e for e in list(df) if re.match('\D+'+str(current_year)+'.+', e)]

    out = pd.DataFrame(zip(
        [current_year for i in current_cols],
#         [current_year for i in range(len(current_cols))],
        current_cols,
        [1/len(current_cols) for current_col in current_cols]
    )
    ).rename(columns = {0:'Year',
                        1:'Ensemble',
                        2:'fracYear'}
            )
    return(out)


ens_weight_df = pd.concat([
    ens_unif_yearwise_weight(
    current_year = e,
    df = enybr_yhats_df) for e in [2021, 2020, 2019, 2018, 2017, 2016, 2015, 2014] 
])


ens_weight_df['Weights'] = ens_weight_df['fracYear'] / np.sum(ens_weight_df['fracYear'])

In [ ]:
ens_weight_df_unif = ens_weight_df

ens_weight_df.reset_index()

index  Year     Ensemble  fracYear  Weights
0       0  2021  enybr2021_1       0.1   0.0125
1       1  2021  enybr2021_8       0.1   0.0125
2       2  2021  enybr2021_3       0.1   0.0125
3       3  2021  enybr2021_0       0.1   0.0125
4       4  2021  enybr2021_2       0.1   0.0125
..    ...   ...          ...       ...      ...
75      5  2014  enybr2014_4       0.1   0.0125
76      6  2014  enybr2014_3       0.1   0.0125
77      7  2014  enybr2014_0       0.1   0.0125
78      8  2014  enybr2014_2       0.1   0.0125
79      9  2014  enybr2014_6       0.1   0.0125

[80 rows x 5 columns]

In [ ]:
def ens_calc_yearwise_rmses(current_year, 
                            df):
    mask = (df.Year == current_year)
    y_true = df.loc[mask, 'Yield_Mg_ha']
    current_cols = [e for e in list(df) if re.match('\D+'+str(current_year)+'.+', e)]

    out = pd.DataFrame(zip(
        [current_year for i in current_cols],
#         [current_year for i in range(len(current_cols))],
        current_cols,
        [mean_squared_error(y_true, df.loc[mask, current_col], squared = False) for current_col in current_cols]
    )
    ).rename(columns = {0:'Year',
                        1:'Ensemble',
                        2:'TestRMSE'}
            )
    return(out)


ens_weight_df = pd.concat([
    ens_calc_yearwise_rmses(
    current_year = e,
    df = enybr_yhats_df) for e in [2021, 2020, 2019, 2018, 2017, 2016, 2015, 2014] 
])

In [ ]:
ens_weight_df['Weights'] = ens_weight_df['TestRMSE']
ens_weight_df['Weights'] = (1/ens_weight_df['Weights'])
ens_weight_df['Weights'] = ens_weight_df['Weights'] / np.sum(ens_weight_df['Weights'])

In [ ]:
ens_weight_df

Year     Ensemble  TestRMSE   Weights
0   2021  enybr2021_1  1.840566  0.010291
1   2021  enybr2021_8  1.844201  0.010271
2   2021  enybr2021_3  1.843636  0.010274
3   2021  enybr2021_0  1.845161  0.010266
4   2021  enybr2021_2  1.839418  0.010298
..   ...          ...       ...       ...
5   2014  enybr2014_4  1.375705  0.013769
6   2014  enybr2014_3  1.364061  0.013886
7   2014  enybr2014_0  1.376079  0.013765
8   2014  enybr2014_2  1.364944  0.013877
9   2014  enybr2014_6  1.372707  0.013799

[80 rows x 4 columns]

In [ ]:
enybr_yhats_df

Env  Year             Hybrid  Yield_Mg_ha  enybr2016_6  \
0      DEH1_2014  2014           B37/MO17    13.074965     5.531932   
1      DEH1_2014  2014           B37/MO17    14.269989     5.531932   
2      DEH1_2014  2014           B37/OH43    12.733455     5.177942   
3      DEH1_2014  2014           B37/OH43    12.888180     5.177942   
4      DEH1_2014  2014           B73/MO17    11.916843     6.977406   
...          ...   ...                ...          ...          ...   
22786  WIH3_2022  2022  W10010_0337/LH244          NaN     8.466721   
22787  WIH3_2022  2022  W10010_0346/LH244          NaN     8.466721   
22788  WIH3_2022  2022  W10010_0358/LH244          NaN     8.466721   
22789  WIH3_2022  2022  W10010_0381/LH244          NaN     8.466721   
22790  WIH3_2022  2022  W10010_0452/LH244          NaN     8.466721   

       enybr2020_9  enybr2015_4  enybr2018_1  enybr2016_5  enybr2018_0  ...  \
0         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
1         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
2         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
3         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
4        10.242690     8.729195    10.017510     7.130188    10.296167  ...   
...            ...          ...          ...          ...          ...  ...   
22786     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22787     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22788     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22789     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22790     9.065231     8.584796     8.757695     8.612560     8.327171  ...   

       enybr2018_7  enybr2018_8  enybr2016_4  enybr2019_8  enybr2015_1  \
0         8.818321     8.744628     5.420871    12.111806     8.031712   
1         8.818321     8.744628     5.420871    12.111806     8.031712   
2         7.945677     7.859318     4.824092    11.049220     7.907455   
3         7.945677     7.859318     4.824092    11.049220     7.907455   
4         9.823241     9.661137     6.576953    12.570122     8.631707   
...            ...          ...          ...          ...          ...   
22786     8.935659     8.222512     8.786011     9.137428     8.964489   
22787     8.935659     8.222512     8.786011     9.137428     8.964489   
22788     8.935659     8.222512     8.786011     9.137428     8.964489   
22789     8.935659     8.222512     8.786011     9.137428     8.964489   
22790     8.935659     8.222512     8.786011     9.137428     8.964489   

       enybr2020_6  enybr2017_3  enybr2014_6  enybr2017_2  enybr2016_8  
0         8.645928     8.236111    13.707251     8.432482     5.097374  
1         8.645928     8.236111    13.707251     8.432482     5.097374  
2         8.866839     7.920904    12.711938     7.810802     5.050909  
3         8.866839     7.920904    12.711938     7.810802     5.050909  
4        10.393625     8.635470    14.786144     8.663692     6.833022  
...            ...          ...          ...          ...          ...  
22786     9.688920     8.459518    11.311052     8.739894     8.355336  
22787     9.688920     8.459518    11.311052     8.739894     8.355336  
22788     9.688920     8.459518    11.311052     8.739894     8.355336  
22789     9.688920     8.459518    11.311052     8.739894     8.355336  
22790     9.688920     8.459518    11.311052     8.739894     8.355336  

[22791 rows x 84 columns]

In [ ]:
# Apply weights and calculate new estimates

tmp = enybr_yhats_df

for ensemble in ens_weight_df.Ensemble:
    weight = float(ens_weight_df.loc[(ens_weight_df.Ensemble == ensemble), 'Weights'])
    tmp.loc[:, ensemble] = tmp.loc[:, ensemble] * weight
    

tmp.loc[:, 'Yhat_Mg_ha_Weighted'] = np.sum(tmp.loc[:, ens_weight_df.Ensemble], axis = 1)

# px.scatter(tmp, x = 'Yield_Mg_ha', y = 'Yhat_Mg_ha_Weighted')

In [ ]:
enybr_yhats_df

Env  Year             Hybrid  Yield_Mg_ha  enybr2016_6  \
0      DEH1_2014  2014           B37/MO17    13.074965     0.083880   
1      DEH1_2014  2014           B37/MO17    14.269989     0.083880   
2      DEH1_2014  2014           B37/OH43    12.733455     0.078512   
3      DEH1_2014  2014           B37/OH43    12.888180     0.078512   
4      DEH1_2014  2014           B73/MO17    11.916843     0.105797   
...          ...   ...                ...          ...          ...   
22786  WIH3_2022  2022  W10010_0337/LH244          NaN     0.128379   
22787  WIH3_2022  2022  W10010_0346/LH244          NaN     0.128379   
22788  WIH3_2022  2022  W10010_0358/LH244          NaN     0.128379   
22789  WIH3_2022  2022  W10010_0381/LH244          NaN     0.128379   
22790  WIH3_2022  2022  W10010_0452/LH244          NaN     0.128379   

       enybr2020_9  enybr2015_4  enybr2018_1  enybr2016_5  enybr2018_0  ...  \
0         0.081734     0.129206     0.116892     0.081517     0.107866  ...   
1         0.081734     0.129206     0.116892     0.081517     0.107866  ...   
2         0.089251     0.118507     0.104197     0.079495     0.103848  ...   
3         0.089251     0.118507     0.104197     0.079495     0.103848  ...   
4         0.111176     0.137097     0.122377     0.107627     0.125553  ...   
...            ...          ...          ...          ...          ...  ...   
22786     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22787     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22788     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22789     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22790     0.098396     0.134830     0.106987     0.130003     0.101543  ...   

       enybr2018_8  enybr2016_4  enybr2019_8  enybr2015_1  enybr2020_6  \
0         0.107548     0.081879     0.131833     0.125887     0.093620   
1         0.107548     0.081879     0.131833     0.125887     0.093620   
2         0.096659     0.072865     0.120267     0.123939     0.096013   
3         0.096659     0.072865     0.120267     0.123939     0.096013   
4         0.118819     0.099341     0.136822     0.135291     0.112545   
...            ...          ...          ...          ...          ...   
22786     0.101126     0.132708     0.099458     0.140507     0.104914   
22787     0.101126     0.132708     0.099458     0.140507     0.104914   
22788     0.101126     0.132708     0.099458     0.140507     0.104914   
22789     0.101126     0.132708     0.099458     0.140507     0.104914   
22790     0.101126     0.132708     0.099458     0.140507     0.104914   

       enybr2017_3  enybr2014_6  enybr2017_2  enybr2016_8  Yhat_Mg_ha_Weighted  
0         0.091852     0.189143     0.094230     0.077407             9.060173  
1         0.091852     0.189143     0.094230     0.077407             9.060173  
2         0.088337     0.175408     0.087283     0.076702             8.573801  
3         0.088337     0.175408     0.087283     0.076702             8.573801  
4         0.096306     0.204030     0.096814     0.103764            10.108102  
...            ...          ...          ...          ...                  ...  
22786     0.094344     0.156078     0.097665     0.126882             9.502741  
22787     0.094344     0.156078     0.097665     0.126882             9.502741  
22788     0.094344     0.156078     0.097665     0.126882             9.502741  
22789     0.094344     0.156078     0.097665     0.126882             9.502741  
22790     0.094344     0.156078     0.097665     0.126882             9.502741  

[22791 rows x 85 columns]

In [ ]:
tmp

Env  Year             Hybrid  Yield_Mg_ha  enybr2016_6  \
0      DEH1_2014  2014           B37/MO17    13.074965     0.083880   
1      DEH1_2014  2014           B37/MO17    14.269989     0.083880   
2      DEH1_2014  2014           B37/OH43    12.733455     0.078512   
3      DEH1_2014  2014           B37/OH43    12.888180     0.078512   
4      DEH1_2014  2014           B73/MO17    11.916843     0.105797   
...          ...   ...                ...          ...          ...   
22786  WIH3_2022  2022  W10010_0337/LH244          NaN     0.128379   
22787  WIH3_2022  2022  W10010_0346/LH244          NaN     0.128379   
22788  WIH3_2022  2022  W10010_0358/LH244          NaN     0.128379   
22789  WIH3_2022  2022  W10010_0381/LH244          NaN     0.128379   
22790  WIH3_2022  2022  W10010_0452/LH244          NaN     0.128379   

       enybr2020_9  enybr2015_4  enybr2018_1  enybr2016_5  enybr2018_0  ...  \
0         0.081734     0.129206     0.116892     0.081517     0.107866  ...   
1         0.081734     0.129206     0.116892     0.081517     0.107866  ...   
2         0.089251     0.118507     0.104197     0.079495     0.103848  ...   
3         0.089251     0.118507     0.104197     0.079495     0.103848  ...   
4         0.111176     0.137097     0.122377     0.107627     0.125553  ...   
...            ...          ...          ...          ...          ...  ...   
22786     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22787     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22788     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22789     0.098396     0.134830     0.106987     0.130003     0.101543  ...   
22790     0.098396     0.134830     0.106987     0.130003     0.101543  ...   

       enybr2018_8  enybr2016_4  enybr2019_8  enybr2015_1  enybr2020_6  \
0         0.107548     0.081879     0.131833     0.125887     0.093620   
1         0.107548     0.081879     0.131833     0.125887     0.093620   
2         0.096659     0.072865     0.120267     0.123939     0.096013   
3         0.096659     0.072865     0.120267     0.123939     0.096013   
4         0.118819     0.099341     0.136822     0.135291     0.112545   
...            ...          ...          ...          ...          ...   
22786     0.101126     0.132708     0.099458     0.140507     0.104914   
22787     0.101126     0.132708     0.099458     0.140507     0.104914   
22788     0.101126     0.132708     0.099458     0.140507     0.104914   
22789     0.101126     0.132708     0.099458     0.140507     0.104914   
22790     0.101126     0.132708     0.099458     0.140507     0.104914   

       enybr2017_3  enybr2014_6  enybr2017_2  enybr2016_8  Yhat_Mg_ha_Weighted  
0         0.091852     0.189143     0.094230     0.077407             9.060173  
1         0.091852     0.189143     0.094230     0.077407             9.060173  
2         0.088337     0.175408     0.087283     0.076702             8.573801  
3         0.088337     0.175408     0.087283     0.076702             8.573801  
4         0.096306     0.204030     0.096814     0.103764            10.108102  
...            ...          ...          ...          ...                  ...  
22786     0.094344     0.156078     0.097665     0.126882             9.502741  
22787     0.094344     0.156078     0.097665     0.126882             9.502741  
22788     0.094344     0.156078     0.097665     0.126882             9.502741  
22789     0.094344     0.156078     0.097665     0.126882             9.502741  
22790     0.094344     0.156078     0.097665     0.126882             9.502741  

[22791 rows x 85 columns]

In [ ]:
# possibility -- todo how similar would submission 2 be relative to one with maximal obs
second_possible_yb = format_submission(
    df = tmp,
    yhat_col = 'Yhat_Mg_ha_Weighted')

In [ ]:
second_possible_yb

Env             Hybrid  Yield_Mg_ha
0      DEH1_2022          B14A/OH43     8.121670
1      DEH1_2022            B37/H95     8.128264
2      DEH1_2022           B73/MO17     9.293124
3      DEH1_2022          B73/PHN82     9.738527
4      DEH1_2022          B73/TX779     8.944199
...          ...                ...          ...
11550  WIH3_2022  W10010_0337/LH244     9.502741
11551  WIH3_2022  W10010_0346/LH244     9.502741
11552  WIH3_2022  W10010_0358/LH244     9.502741
11553  WIH3_2022  W10010_0381/LH244     9.502741
11554  WIH3_2022  W10010_0452/LH244     9.502741

[11555 rows x 3 columns]

In [ ]:
# Uses historical data
# uses rf aggregation
# uses inverse rmse weighting on cv aggs
second_submission = second_possible_yb
if False:
    second_submission.to_csv('./notebook_artifacts/99_submissions/Submission_2.csv', index = 'False')

In [ ]:
# Compare the two submissions: 
px.scatter(
    pd.DataFrame(zip(
        first_submission.Yield_Mg_ha, 
        second_possible_yb.Yield_Mg_ha
    )).rename(columns = {0:'s1', 1:'s2'}),
    x = 's1', y = 's2')

In [ ]:
## Submission 3 ==============================================================
enybr_yhats_df = enybr_yhats_df_backup
enybr_yhats_df

Env  Year             Hybrid  Yield_Mg_ha  enybr2016_6  \
0      DEH1_2014  2014           B37/MO17    13.074965     5.531932   
1      DEH1_2014  2014           B37/MO17    14.269989     5.531932   
2      DEH1_2014  2014           B37/OH43    12.733455     5.177942   
3      DEH1_2014  2014           B37/OH43    12.888180     5.177942   
4      DEH1_2014  2014           B73/MO17    11.916843     6.977406   
...          ...   ...                ...          ...          ...   
22786  WIH3_2022  2022  W10010_0337/LH244          NaN     8.466721   
22787  WIH3_2022  2022  W10010_0346/LH244          NaN     8.466721   
22788  WIH3_2022  2022  W10010_0358/LH244          NaN     8.466721   
22789  WIH3_2022  2022  W10010_0381/LH244          NaN     8.466721   
22790  WIH3_2022  2022  W10010_0452/LH244          NaN     8.466721   

       enybr2020_9  enybr2015_4  enybr2018_1  enybr2016_5  enybr2018_0  ...  \
0         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
1         7.530155     8.226755     9.568493     5.400436     8.845741  ...   
2         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
3         8.222730     7.545486     8.529356     5.266490     8.516252  ...   
4        10.242690     8.729195    10.017510     7.130188    10.296167  ...   
...            ...          ...          ...          ...          ...  ...   
22786     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22787     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22788     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22789     9.065231     8.584796     8.757695     8.612560     8.327171  ...   
22790     9.065231     8.584796     8.757695     8.612560     8.327171  ...   

       enybr2018_7  enybr2018_8  enybr2016_4  enybr2019_8  enybr2015_1  \
0         8.818321     8.744628     5.420871    12.111806     8.031712   
1         8.818321     8.744628     5.420871    12.111806     8.031712   
2         7.945677     7.859318     4.824092    11.049220     7.907455   
3         7.945677     7.859318     4.824092    11.049220     7.907455   
4         9.823241     9.661137     6.576953    12.570122     8.631707   
...            ...          ...          ...          ...          ...   
22786     8.935659     8.222512     8.786011     9.137428     8.964489   
22787     8.935659     8.222512     8.786011     9.137428     8.964489   
22788     8.935659     8.222512     8.786011     9.137428     8.964489   
22789     8.935659     8.222512     8.786011     9.137428     8.964489   
22790     8.935659     8.222512     8.786011     9.137428     8.964489   

       enybr2020_6  enybr2017_3  enybr2014_6  enybr2017_2  enybr2016_8  
0         8.645928     8.236111    13.707251     8.432482     5.097374  
1         8.645928     8.236111    13.707251     8.432482     5.097374  
2         8.866839     7.920904    12.711938     7.810802     5.050909  
3         8.866839     7.920904    12.711938     7.810802     5.050909  
4        10.393625     8.635470    14.786144     8.663692     6.833022  
...            ...          ...          ...          ...          ...  
22786     9.688920     8.459518    11.311052     8.739894     8.355336  
22787     9.688920     8.459518    11.311052     8.739894     8.355336  
22788     9.688920     8.459518    11.311052     8.739894     8.355336  
22789     9.688920     8.459518    11.311052     8.739894     8.355336  
22790     9.688920     8.459518    11.311052     8.739894     8.355336  

[22791 rows x 84 columns]

In [ ]:
# Apply weights and calculate new estimates

tmp = enybr_yhats_df

for ensemble in ens_weight_df_unif.Ensemble:
    weight = float(ens_weight_df_unif.loc[(ens_weight_df_unif.Ensemble == ensemble), 'Weights'])
    tmp.loc[:, ensemble] = tmp.loc[:, ensemble] * weight
    

tmp.loc[:, 'Yhat_Mg_ha_Weighted'] = np.sum(tmp.loc[:, ens_weight_df_unif.Ensemble], axis = 1)

In [ ]:
third_possible_yb = format_submission(
    df = tmp,
    yhat_col = 'Yhat_Mg_ha_Weighted')

In [ ]:
# Uses historical data
# uses rf aggregation
# uses uniform weighting on cv aggs
third_submission = third_possible_yb
if False:
    third_submission.to_csv('./notebook_artifacts/99_submissions/Submission_3.csv', index = 'False')
    third_submission.to_csv('./notebook_artifacts/99_submissions/Submission_3_enybr_uw.csv')

In [ ]:
# Compare the two submissions: 
px.scatter(
    pd.DataFrame(zip(
        third_possible_yb.Yield_Mg_ha, 
        second_possible_yb.Yield_Mg_ha
    )).rename(columns = {0:'s1', 1:'s2'}),
    x = 's1', y = 's2')

### Feed into DNN

In [ ]:
EMatNames[-1]

'hist2018_2YHats.csv'

In [ ]:
[e.shape for e in [yHats_yesBlup, yHats_notBlup]]

[(22791, 293), (125620, 244)]

In [ ]:
[e.shape for e in [phno, YMat, GMat, SMat, WMat, MMat, EMat]]
# yHats_yesBlup, 

[(22791, 5),
 (22791,),
 (22791, 2250),
 (22791, 23),
 (22791, 16, 314),
 (22791, 765),
 (22791, 288)]

## yHats_noBlup

In [ ]:
yHats_notBlup

Env  Year             Hybrid  Yield_Mg_ha   rf2017_5   rf2016_8  \
0       DEH1_2014  2014        M0088/LH185     5.721725  10.591565  11.412896   
1       DEH1_2014  2014        M0143/LH185    11.338246  11.995944  11.639840   
2       DEH1_2014  2014        M0003/LH185     6.540810  10.605881  11.549416   
3       DEH1_2014  2014        M0035/LH185    10.366857  11.623779  11.524263   
4       DEH1_2014  2014        M0052/LH185    10.908814  12.024014  11.639840   
...           ...   ...                ...          ...        ...        ...   
125615  WIH3_2022  2022  W10010_0337/LH244          NaN   9.869797   4.570224   
125616  WIH3_2022  2022  W10010_0346/LH244          NaN   9.869797   4.570224   
125617  WIH3_2022  2022  W10010_0358/LH244          NaN   9.869797   4.570224   
125618  WIH3_2022  2022  W10010_0381/LH244          NaN   9.869797   4.570224   
125619  WIH3_2022  2022  W10010_0452/LH244          NaN   9.869797   4.570224   

         rf2015_4   rf2019_3   rf2020_8   rf2016_1  ...  hist2020_5YHats.csv  \
0       11.685779  11.641665  12.045789  11.209850  ...            11.288484   
1       11.685779  11.922401  12.045789  11.623760  ...            12.070378   
2       11.685779  11.887824  12.045789  11.398859  ...            11.656081   
3       11.685779  11.901552  12.045789  11.539536  ...            12.070378   
4       11.685779  11.922401  12.045789  11.621606  ...            12.070378   
...           ...        ...        ...        ...  ...                  ...   
125615  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125616  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125617  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125618  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125619  10.476830  11.017629   9.682651   4.907785  ...             9.365567   

        hist2016_7YHats.csv  hist2017_2YHats.csv  hist2018_4YHats.csv  \
0                 11.458952            10.827850             9.858067   
1                 12.027027            12.007756            12.109882   
2                 11.503217            11.314791            10.627190   
3                 12.027027            12.007756            11.057308   
4                 12.027027            12.007756            12.077585   
...                     ...                  ...                  ...   
125615             7.675474            10.163933            10.004684   
125616             7.675474            10.163933            10.004684   
125617             7.675474            10.163933            10.004684   
125618             7.675474            10.163933            10.004684   
125619             7.675474            10.163933            10.004684   

        hist2016_2YHats.csv  hist2015_7YHats.csv  hist2017_1YHats.csv  \
0                 11.636543             9.789523            10.685014   
1                 12.130605            12.070672            12.087270   
2                 12.130605            11.681806            11.087559   
3                 12.130605            11.938285            12.040407   
4                 12.130605            12.070672            12.087270   
...                     ...                  ...                  ...   
125615             6.896305            10.585495            10.264088   
125616             6.896305            10.585495            10.264088   
125617             6.896305            10.585495            10.264088   
125618             6.896305            10.585495            10.264088   
125619             6.896305            10.585495            10.264088   

        hist2015_5YHats.csv  hist2016_8YHats.csv  hist2018_2YHats.csv  
0                 10.988976            12.000669             9.811252  
1                 12.079331            12.134541            12.048985  
2                 11.621269            11.682847             9.988564  
3                 12.079331           

In [ ]:
idxs_with_hist = list(
    yHats_notBlup.merge(phno.reset_index(), 
                        how = 'inner'
                       ).drop_duplicates().loc[:, 'index'])

In [ ]:
phno, YMat, GMat, SMat, WMat, MMat = restrict_mats(
    phno_idxs = idxs_with_hist, #[], # list of indices to be used. If [] passed make no change
    # here restrict to suset that historical coud be calc-ed for
    phno = phno_backup,
    YMat = YMat_backup,
    GMat = GMat_backup,
    SMat = SMat_backup,
    WMat = WMat_backup,
    MMat = MMat_backup)

### Simplest thing that might work

Average with respect to 
Within model type
within hold out year
across hold out years

In [ ]:
ens_cols = [e for e in list(yHats_yesBlup) if e not in ['phno_Idx', 'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']]
# Specifying prefix allows for reproducibility without hardcoding
ens_cols = [e for e in ens_cols if  re.match('^[rf\d\d\d\d_\d|xgb\d\d\d\d_\d]', e)]
ens_cols

ens_cols_info = pd.DataFrame(zip(
    ens_cols,
    [re.findall('\d\d\d\d', e)[0] for e in list(ens_cols)],
    [re.findall('^\D+', e)[0] for e in list(ens_cols)],
    [re.findall('\d+$', e)[0] for e in list(ens_cols)]
)).rename(columns = {0:'Model_Name', 1:'Holdout_Year', 2:'Model', 3:'Rep',})

ens_cols_info

tmp = yHats_yesBlup

id_vars = ['phno_Idx', 'Env', 'Hybrid', 'Year']

tmp = tmp.melt(id_vars=id_vars, 
               value_vars=[e for e in list(tmp) if e not in id_vars],
               var_name='Model_Name', value_name='yHat')

tmp = tmp.merge(ens_cols_info, how = 'left')

tmp.head(5)

phno_Idx        Env    Hybrid  Year   Model_Name       yHat Holdout_Year  \
0       442  DEH1_2014  B37/MO17  2014  Yield_Mg_ha  13.074965          NaN   
1       170  DEH1_2014  B37/MO17  2014  Yield_Mg_ha  14.269989          NaN   
2       443  DEH1_2014  B37/OH43  2014  Yield_Mg_ha  12.733455          NaN   
3       159  DEH1_2014  B37/OH43  2014  Yield_Mg_ha  12.888180          NaN   
4       154  DEH1_2014  B73/MO17  2014  Yield_Mg_ha  11.916843          NaN   

  Model  Rep  
0   NaN  NaN  
1   NaN  NaN  
2   NaN  NaN  
3   NaN  NaN  
4   NaN  NaN

In [ ]:
# average replicates
tmp = tmp.groupby(id_vars+['Holdout_Year', 'Model']).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year Holdout_Year Model       yHat
0       153  DEH1_2014  PHG39/PHN82  2014         2014    rf   8.443935
1       153  DEH1_2014  PHG39/PHN82  2014         2014   xgb   9.375648
2       153  DEH1_2014  PHG39/PHN82  2014         2015    rf  11.738493
3       153  DEH1_2014  PHG39/PHN82  2014         2015   xgb   9.807565
4       153  DEH1_2014  PHG39/PHN82  2014         2016    rf  11.659393

In [ ]:
# average over model types
tmp = tmp.groupby(id_vars+['Holdout_Year']).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year Holdout_Year       yHat
0       153  DEH1_2014  PHG39/PHN82  2014         2014   8.909791
1       153  DEH1_2014  PHG39/PHN82  2014         2015  10.773029
2       153  DEH1_2014  PHG39/PHN82  2014         2016  10.707765
3       153  DEH1_2014  PHG39/PHN82  2014         2017  11.061713
4       153  DEH1_2014  PHG39/PHN82  2014         2018  10.890765

In [ ]:
# average over holdout years
tmp = tmp.groupby(id_vars).agg(yHat = ('yHat', np.mean)).reset_index().drop_duplicates()
tmp.head()

phno_Idx        Env       Hybrid  Year       yHat
0       153  DEH1_2014  PHG39/PHN82  2014  10.630590
1       154  DEH1_2014     B73/MO17  2014  12.932911
2       156  DEH1_2014  PHW52/PHM49  2014  11.768988
3       157  DEH1_2014    B73/PHN82  2014  12.154508
4       158  DEH1_2014   LH74/PHN82  2014  11.497086

In [ ]:
tmp

phno_Idx        Env             Hybrid  Year       yHat
0           153  DEH1_2014        PHG39/PHN82  2014  10.630590
1           154  DEH1_2014           B73/MO17  2014  12.932911
2           156  DEH1_2014        PHW52/PHM49  2014  11.768988
3           157  DEH1_2014          B73/PHN82  2014  12.154508
4           158  DEH1_2014         LH74/PHN82  2014  11.497086
...         ...        ...                ...   ...        ...
22786    138258  WIH3_2022  W10010_0337/LH244  2022   9.454343
22787    138259  WIH3_2022  W10010_0346/LH244  2022   9.454343
22788    138260  WIH3_2022  W10010_0358/LH244  2022   9.454343
22789    138261  WIH3_2022  W10010_0381/LH244  2022   9.454343
22790    138262  WIH3_2022  W10010_0452/LH244  2022   9.454343

[22791 rows x 5 columns]

In [ ]:
first_counterfactual_submission = format_submission(
    df = tmp,
    yhat_col = 'yHat')

In [ ]:
# Compare the two submissions: 
px.scatter(
    pd.DataFrame(zip(
        first_submission.Yield_Mg_ha, 
        first_counterfactual_submission.Yield_Mg_ha
    )).rename(columns = {0:'s1', 1:'s1prime'}),
    x = 's1', y = 's1prime')

In [ ]:
# all non blups
# uniform weights (better than the weights in sub 2)
if False:
    # first_counterfactual_submission.to_csv('./notebook_artifacts/99_submissions/Submission_4.csv', index = 'False')
    first_counterfactual_submission.to_csv('./notebook_artifacts/99_submissions/Submission_4_ennbu_uw.csv')

### Test with RF (unoptimized)

In [ ]:
yHats_notBlup

Env  Year             Hybrid  Yield_Mg_ha   rf2017_5   rf2016_8  \
0       DEH1_2014  2014        M0088/LH185     5.721725  10.591565  11.412896   
1       DEH1_2014  2014        M0143/LH185    11.338246  11.995944  11.639840   
2       DEH1_2014  2014        M0003/LH185     6.540810  10.605881  11.549416   
3       DEH1_2014  2014        M0035/LH185    10.366857  11.623779  11.524263   
4       DEH1_2014  2014        M0052/LH185    10.908814  12.024014  11.639840   
...           ...   ...                ...          ...        ...        ...   
125615  WIH3_2022  2022  W10010_0337/LH244          NaN   9.869797   4.570224   
125616  WIH3_2022  2022  W10010_0346/LH244          NaN   9.869797   4.570224   
125617  WIH3_2022  2022  W10010_0358/LH244          NaN   9.869797   4.570224   
125618  WIH3_2022  2022  W10010_0381/LH244          NaN   9.869797   4.570224   
125619  WIH3_2022  2022  W10010_0452/LH244          NaN   9.869797   4.570224   

         rf2015_4   rf2019_3   rf2020_8   rf2016_1  ...  hist2020_5YHats.csv  \
0       11.685779  11.641665  12.045789  11.209850  ...            11.288484   
1       11.685779  11.922401  12.045789  11.623760  ...            12.070378   
2       11.685779  11.887824  12.045789  11.398859  ...            11.656081   
3       11.685779  11.901552  12.045789  11.539536  ...            12.070378   
4       11.685779  11.922401  12.045789  11.621606  ...            12.070378   
...           ...        ...        ...        ...  ...                  ...   
125615  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125616  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125617  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125618  10.476830  11.017629   9.682651   4.907785  ...             9.365567   
125619  10.476830  11.017629   9.682651   4.907785  ...             9.365567   

        hist2016_7YHats.csv  hist2017_2YHats.csv  hist2018_4YHats.csv  \
0                 11.458952            10.827850             9.858067   
1                 12.027027            12.007756            12.109882   
2                 11.503217            11.314791            10.627190   
3                 12.027027            12.007756            11.057308   
4                 12.027027            12.007756            12.077585   
...                     ...                  ...                  ...   
125615             7.675474            10.163933            10.004684   
125616             7.675474            10.163933            10.004684   
125617             7.675474            10.163933            10.004684   
125618             7.675474            10.163933            10.004684   
125619             7.675474            10.163933            10.004684   

        hist2016_2YHats.csv  hist2015_7YHats.csv  hist2017_1YHats.csv  \
0                 11.636543             9.789523            10.685014   
1                 12.130605            12.070672            12.087270   
2                 12.130605            11.681806            11.087559   
3                 12.130605            11.938285            12.040407   
4                 12.130605            12.070672            12.087270   
...                     ...                  ...                  ...   
125615             6.896305            10.585495            10.264088   
125616             6.896305            10.585495            10.264088   
125617             6.896305            10.585495            10.264088   
125618             6.896305            10.585495            10.264088   
125619             6.896305            10.585495            10.264088   

        hist2015_5YHats.csv  hist2016_8YHats.csv  hist2018_2YHats.csv  
0                 10.988976            12.000669             9.811252  
1                 12.079331            12.134541            12.048985  
2                 11.621269            11.682847             9.988564  
3                 12.079331           

In [ ]:
EMat = np.array(yHats_notBlup.drop(columns = [#'phno_Idx', 
    'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']))
EMatNames =list(yHats_notBlup.drop(columns = [#'phno_Idx', 
    'Env', 'Hybrid', 'Year', 'Yield_Mg_ha']))

In [ ]:
test_x_2d_names = list(GMatNames)+list(SMatNames)+list(WMatNames)+list(MMatNames)+list(EMatNames)

In [ ]:
# Setup ----------------------------------------------------------------------
trial_name = 'ennbr' # ensemble, no blup, random forest
n_trials= 40 #FIXME
n_jobs = 20  #FIXME

downsample = False
downsample_train = 1000
downsample_test  =  100

def objective(trial): 
    rf_max_depth = trial.suggest_int('rf_max_depth', 2, 100, log=True)
    rf_n_estimators = trial.suggest_int('rf_n_estimators', 20, 100, log=True)
    rf_min_samples_split = trial.suggest_float('rf_min_samples_split', 0.005, 0.5, log=True)
    
    regr = RandomForestRegressor(
        max_depth = rf_max_depth, 
        n_estimators = rf_n_estimators,
        min_samples_split = rf_min_samples_split
        )
    
#     rf = regr.fit(train_x_2d, train_y_1d)
#     return (mean_squared_error(train_y_1d, rf.predict(train_x_2d), squared=False))
    rf = regr.fit(test_x_2d, test_y_1d)
    return (mean_squared_error(test_y_1d, rf.predict(test_x_2d), squared=False))

if False:
    reset_trial_name = trial_name
    print("""
    ------------------------------------------------------------------------------
               Note: Ensemble fit using previous test fold.
    ------------------------------------------------------------------------------
    """)
    for test_this_year in ['2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021']:
        print("""
    ------------------------------------------
    ------------------"""+test_this_year+"""------------------
        """)    

        trial_name = reset_trial_name
        trial_name = trial_name+test_this_year
        print(test_this_year)
        # Data Prep. -----------------------------------------------------------------
        # Set up train/test indices --------------------------------------------------
        train_x_2d, train_y_1d, test_x_2d, test_y_1d, full_x_2d, YMat_center, YMat_scale, YMat = prep_ensemble_train_test(
                test_this_year = test_this_year,
                downsample = downsample, 
                downsample_train = downsample_train,
                downsample_test  =  downsample_test,
                phno = phno,
                GMat = GMat,
                SMat = SMat,
                WMat = WMat,
                MMat = MMat,
                EMat = EMat,
                YMat = YMat)

        test_year_cols = get_non_cv_cols(
            test_this_year = test_this_year,
            EMatNames = EMatNames,
            test_x_2d_names = test_x_2d_names)

        # excise columns that would allow for information leakage into the 
        train_x_2d = train_x_2d[:, np.array(test_year_cols)]
        test_x_2d  =  test_x_2d[:, np.array(test_year_cols)]
        full_x_2d  =  full_x_2d[:, np.array(test_year_cols)]


        # HPS Study ------------------------------------------------------------------
        cache_save_name = cache_path+trial_name+'_hps.pkl'
        if os.path.exists(cache_save_name):
            study = pkl.load(open(cache_save_name, 'rb'))  
        else:
            study = optuna.create_study(direction="minimize")
            study.optimize(objective, n_trials= n_trials, n_jobs = n_jobs)
            # save    
            pkl.dump(study, open(cache_save_name, 'wb'))    

        print("""
    --------------Study Complete--------------
    ------------------------------------------
        """)
        def fit_single_rep(Rep = 1):
            # Fit Best HPS --------------------------------------------------------------- 
            cache_save_name = cache_path+trial_name+'_'+str(Rep)+'_mod.pkl'

            # Load cached model if it exists
            if os.path.exists(cache_save_name):
                rf = pkl.load(open(cache_save_name, 'rb'))  
            else:
                regr = RandomForestRegressor(
                        max_depth = study.best_trial.params['rf_max_depth'], 
                        n_estimators = study.best_trial.params['rf_n_estimators'],
                        min_samples_split = study.best_trial.params['rf_min_samples_split']
                        )
    #             rf = regr.fit(train_x_2d, train_y_1d)
                rf = regr.fit(test_x_2d, test_y_1d)
                # save    
                pkl.dump(rf, open(cache_save_name, 'wb'))   

            # Record Predictions -----------------------------------------------------
            out = phno.copy()
            out['YHat'] = rf.predict(full_x_2d)
            out['YMat'] = YMat
            out['Y_center'] = YMat_center
            out['Y_scale'] = YMat_scale
            out['Class'] = trial_name
            out['CV'] = test_this_year
            out['Rep'] = Rep
            out.to_csv('./notebook_artifacts/5_ensembling/'+trial_name+'_'+str(Rep)+'YHats.csv')
    #         out.to_csv('./data/Shared_Model_Output/'+trial_name+'_'+str(Rep)+'rfYHats.csv')

        # use joblib to get replicate models all at once
        Parallel(n_jobs=10)(delayed(fit_single_rep)(Rep = i) for i in range(10))

In [ ]:
ennbr_yhats = [e for e in os.listdir(cache_path) if re.match('ennbr\d\d\d\d_\dYHats.csv', e)] 

# aggregate all ennbr predictions
# pull select cols from each file then merge
ennbr_yhats_df = [get_ml_yhats(file_name = ennbr_yhat,
                               rename_Yhat = ennbr_yhat.replace('YHats.csv', ''),
                               file_path = cache_path
                ) for ennbr_yhat in tqdm.tqdm(ennbr_yhats)]

# This is messy but the alternative is to repeatedly merge
# drop select cols from all but 0th data frame so they are not duplicated in 
# in the yhat df
ennbr_yhats_df = pd.concat([ennbr_yhats_df[e] if e == 0 else 
                         ennbr_yhats_df[e].drop(columns = [
                             'Env', 'Year', 'Hybrid', 'Yield_Mg_ha']) 
                         for e in range(0, len(ennbr_yhats_df))], axis = 1)

ennbr_yhats_df

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 80/80 [00:10<00:00,  7.86it/s]


Env  Year             Hybrid  Yield_Mg_ha  ennbr2020_5  \
0       DEH1_2014  2014        M0088/LH185     5.721725     9.116123   
1       DEH1_2014  2014        M0143/LH185    11.338246     9.116123   
2       DEH1_2014  2014        M0003/LH185     6.540810     9.116123   
3       DEH1_2014  2014        M0035/LH185    10.366857     9.116123   
4       DEH1_2014  2014        M0052/LH185    10.908814     9.116123   
...           ...   ...                ...          ...          ...   
125615  WIH3_2022  2022  W10010_0337/LH244          NaN     8.853676   
125616  WIH3_2022  2022  W10010_0346/LH244          NaN     8.853676   
125617  WIH3_2022  2022  W10010_0358/LH244          NaN     8.853676   
125618  WIH3_2022  2022  W10010_0381/LH244          NaN     8.853676   
125619  WIH3_2022  2022  W10010_0452/LH244          NaN     8.853676   

        ennbr2019_4  ennbr2020_9  ennbr2017_8  ennbr2016_0  ennbr2015_6  ...  \
0          8.326604     8.913193     9.486157     6.704530     8.341612  ...   
1          8.326604     8.913193     9.486157     6.704530     8.341612  ...   
2          8.326604     8.913193     9.486157     6.704530     8.341612  ...   
3          8.326604     8.913193     9.486157     6.704530     8.341612  ...   
4          8.326604     8.913193     9.486157     6.704530     8.420423  ...   
...             ...          ...          ...          ...          ...  ...   
125615     8.023043     8.615757     9.653085     8.918329     8.534462  ...   
125616     8.023043     8.615757     9.653085     8.918329     8.534462  ...   
125617     8.023043     8.615757     9.653085     8.918329     8.534462  ...   
125618     8.023043     8.615757     9.653085     8.918329     8.534462  ...   
125619     8.023043     8.615757     9.653085     8.918329     8.534462  ...   

        ennbr2015_8  ennbr2018_6  ennbr2018_2  ennbr2014_9  ennbr2019_3  \
0          8.611613    10.910992    10.632782    10.122334     8.185543   
1          8.660286    10.910992    10.632782    12.323458     8.185543   
2          8.611613    10.910992    10.632782    10.909534     8.185543   
3          8.611613    10.910992    10.632782    10.652798     8.185543   
4          8.260342    10.910992    10.632782    11.765318     8.185543   
...             ...          ...          ...          ...          ...   
125615     8.398534    10.337100    10.258730     8.442426     7.878556   
125616     8.398534    10.337100    10.258730     8.442426     7.878556   
125617     8.398534    10.337100    10.258730     8.442426     7.878556   
125618     8.398534    10.337100    10.258730     8.442426     7.878556   
125619     8.398534    10.337100    10.258730     8.442426     7.878556   

        ennbr2019_5  ennbr2021_0  ennbr2016_1  ennbr2021_7  ennbr2017_1  
0          9.590223    10.994012     7.065589    10.734325     9.130659  
1          9.590223    10.994012     7.065589    10.734325     9.130659  
2          9.590223    10.994012     7.065589    10.734325     9.130659  
3          9.590223    10.994012     7.065589    10.734325     9.130659  
4          9.590223    10.994012     7.065589    10.734325     9.130659  
...             ...          ...          ...          ...          ...  
125615     9.696852    11.819213     8.882016    12.264557     9.267578  
125616     9.696852    11.819213     8.882016    12.264557     9.267578  
125617     9.696852    11.819213     8.882016    12.264557     9.267578  
125618     9.696852    11.819213     8.882016    12.264557     9.267578  
125619     9.696852    11.819213     8.882016    12.264557     9.267578  

[125620 rows x 84 columns]

In [ ]:
# uniform weights

ens_weight_df = pd.concat([
    ens_unif_yearwise_weight(
    current_year = e,
    df = ennbr_yhats_df) for e in [2021, 2020, 2019, 2018, 2017, 2016, 2015, 2014] 
])


ens_weight_df['Weights'] = ens_weight_df['fracYear'] / np.sum(ens_weight_df['fracYear'])
ens_weight_df.reset_index()

index  Year     Ensemble  fracYear  Weights
0       0  2021  ennbr2021_2       0.1   0.0125
1       1  2021  ennbr2021_4       0.1   0.0125
2       2  2021  ennbr2021_5       0.1   0.0125
3       3  2021  ennbr2021_6       0.1   0.0125
4       4  2021  ennbr2021_9       0.1   0.0125
..    ...   ...          ...       ...      ...
75      5  2014  ennbr2014_5       0.1   0.0125
76      6  2014  ennbr2014_7       0.1   0.0125
77      7  2014  ennbr2014_3       0.1   0.0125
78      8  2014  ennbr2014_1       0.1   0.0125
79      9  2014  ennbr2014_9       0.1   0.0125

[80 rows x 5 columns]

In [ ]:
# Apply weights and calculate new estimates

tmp = ennbr_yhats_df

for ensemble in ens_weight_df.Ensemble:
    weight = float(ens_weight_df.loc[(ens_weight_df.Ensemble == ensemble), 'Weights'])
    tmp.loc[:, ensemble] = tmp.loc[:, ensemble] * weight
    

tmp.loc[:, 'Yhat_Mg_ha_Weighted'] = np.sum(tmp.loc[:, ens_weight_df.Ensemble], axis = 1)

# px.scatter(tmp, x = 'Yield_Mg_ha', y = 'Yhat_Mg_ha_Weighted')

In [ ]:
tmp

Env  Year             Hybrid  Yield_Mg_ha  ennbr2020_5  \
0       DEH1_2014  2014        M0088/LH185     5.721725     0.113952   
1       DEH1_2014  2014        M0143/LH185    11.338246     0.113952   
2       DEH1_2014  2014        M0003/LH185     6.540810     0.113952   
3       DEH1_2014  2014        M0035/LH185    10.366857     0.113952   
4       DEH1_2014  2014        M0052/LH185    10.908814     0.113952   
...           ...   ...                ...          ...          ...   
125615  WIH3_2022  2022  W10010_0337/LH244          NaN     0.110671   
125616  WIH3_2022  2022  W10010_0346/LH244          NaN     0.110671   
125617  WIH3_2022  2022  W10010_0358/LH244          NaN     0.110671   
125618  WIH3_2022  2022  W10010_0381/LH244          NaN     0.110671   
125619  WIH3_2022  2022  W10010_0452/LH244          NaN     0.110671   

        ennbr2019_4  ennbr2020_9  ennbr2017_8  ennbr2016_0  ennbr2015_6  ...  \
0          0.104083     0.111415     0.118577     0.083807     0.104270  ...   
1          0.104083     0.111415     0.118577     0.083807     0.104270  ...   
2          0.104083     0.111415     0.118577     0.083807     0.104270  ...   
3          0.104083     0.111415     0.118577     0.083807     0.104270  ...   
4          0.104083     0.111415     0.118577     0.083807     0.105255  ...   
...             ...          ...          ...          ...          ...  ...   
125615     0.100288     0.107697     0.120664     0.111479     0.106681  ...   
125616     0.100288     0.107697     0.120664     0.111479     0.106681  ...   
125617     0.100288     0.107697     0.120664     0.111479     0.106681  ...   
125618     0.100288     0.107697     0.120664     0.111479     0.106681  ...   
125619     0.100288     0.107697     0.120664     0.111479     0.106681  ...   

        ennbr2018_6  ennbr2018_2  ennbr2014_9  ennbr2019_3  ennbr2019_5  \
0          0.136387     0.132910     0.126529     0.102319     0.119878   
1          0.136387     0.132910     0.154043     0.102319     0.119878   
2          0.136387     0.132910     0.136369     0.102319     0.119878   
3          0.136387     0.132910     0.133160     0.102319     0.119878   
4          0.136387     0.132910     0.147066     0.102319     0.119878   
...             ...          ...          ...          ...          ...   
125615     0.129214     0.128234     0.105530     0.098482     0.121211   
125616     0.129214     0.128234     0.105530     0.098482     0.121211   
125617     0.129214     0.128234     0.105530     0.098482     0.121211   
125618     0.129214     0.128234     0.105530     0.098482     0.121211   
125619     0.129214     0.128234     0.105530     0.098482     0.121211   

        ennbr2021_0  ennbr2016_1  ennbr2021_7  ennbr2017_1  \
0          0.137425     0.088320     0.134179     0.114133   
1          0.137425     0.088320     0.134179     0.114133   
2          0.137425     0.088320     0.134179     0.114133   
3          0.137425     0.088320     0.134179     0.114133   
4          0.137425     0.088320     0.134179     0.114133   
...             ...          ...          ...          ...   
125615     0.147740     0.111025     0.153307     0.115845   
125616     0.147740     0.111025     0.153307     0.115845   
125617     0.147740     0.111025     0.153307     0.115845   
125618     0.147740     0.111025     0.153307     0.115845   
125619     0.147740     0.111025     0.153307     0.115845   

        Yhat_Mg_ha_Weighted  
0                  9.299026  
1                  9.582749  
2                  9.398442  
3                  9.404031  
4                  9.504434  
...                     ...  
125615             9.443206  
125616             9.443206  
125617             9.443206  
125618             9.443206  
125619             9.443206  

[125620 rows x 85 columns]

In [ ]:
# possibility -- todo how similar would submission 2 be relative to one with maximal obs
thrid_possible_nb = format_submission(
    df = tmp,
    yhat_col = 'Yhat_Mg_ha_Weighted')

In [ ]:
# Compare the two submissions: 
px.scatter(
    pd.DataFrame(zip(
        first_submission.Yield_Mg_ha, 
        thrid_possible_nb.Yield_Mg_ha
    )).rename(columns = {0:'s1', 1:'s1prime'}),
    x = 's1', y = 's1prime')

In [ ]:
# No blups
# rf, equal weighting
if False:
    thrid_possible_nb.to_csv('./notebook_artifacts/99_submissions/Submission_4.csv')
    thrid_possible_nb.to_csv('./notebook_artifacts/99_submissions/Submission_4_ennbr_uw.csv')

In [ ]:
# Compare the two submissions: 
px.scatter(
    pd.DataFrame(zip(
        first_submission.Yield_Mg_ha, 
        thrid_possible_nb.Yield_Mg_ha
    )).rename(columns = {0:'s1', 1:'s2'}),
    x = 's1', y = 's2')